In [3]:
import numpy as np # library to handle data in a vectorized manner

import pandas as pd # library for data analsysis
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)

import json # library to handle JSON files

!conda install -c conda-forge geopy --yes # uncomment this line if you haven't completed the Foursquare API lab
from geopy.geocoders import Nominatim # convert an address into latitude and longitude values

import requests # library to handle requests
from pandas.io.json import json_normalize # tranform JSON file into a pandas dataframe

# Matplotlib and associated plotting modules
import matplotlib.cm as cm
import matplotlib.colors as colors

# import k-means from clustering stage
from sklearn.cluster import KMeans

#!conda install -c conda-forge folium=0.5.0 --yes # uncomment this line if you haven't completed the Foursquare API lab
import folium # map rendering library

print('Libraries imported.')

Solving environment: done

# All requested packages already installed.

Libraries imported.


In [4]:
!wget -q -O 'newyork_data.json' https://cf-courses-data.s3.us.cloud-object-storage.appdomain.cloud/IBMDeveloperSkillsNetwork-DS0701EN-SkillsNetwork/labs/newyork_data.json
with open('newyork_data.json') as json_data:
    newyork_data = json.load(json_data)

In [5]:
neighborhoods_data = newyork_data['features']
neighborhoods_data[0]

{'type': 'Feature',
 'id': 'nyu_2451_34572.1',
 'geometry': {'type': 'Point',
  'coordinates': [-73.84720052054902, 40.89470517661]},
 'geometry_name': 'geom',
 'properties': {'name': 'Wakefield',
  'stacked': 1,
  'annoline1': 'Wakefield',
  'annoline2': None,
  'annoline3': None,
  'annoangle': 0.0,
  'borough': 'Bronx',
  'bbox': [-73.84720052054902,
   40.89470517661,
   -73.84720052054902,
   40.89470517661]}}

In [6]:
# define the dataframe columns
column_names = ['Borough', 'Neighborhood', 'Latitude', 'Longitude'] 

# instantiate the dataframe
neighborhoods = pd.DataFrame(columns=column_names)
for data in neighborhoods_data:
    borough = neighborhood_name = data['properties']['borough'] 
    neighborhood_name = data['properties']['name']
        
    neighborhood_latlon = data['geometry']['coordinates']
    neighborhood_lat = neighborhood_latlon[1]
    neighborhood_lon = neighborhood_latlon[0]
    
    neighborhoods = neighborhoods.append({'Borough': borough,
                                          'Neighborhood': neighborhood_name,
                                          'Latitude': neighborhood_lat,
                                          'Longitude': neighborhood_lon}, ignore_index=True)

In [7]:
neighborhoods.head()

Borough Neighborhood   Latitude  Longitude
0   Bronx    Wakefield  40.894705 -73.847201
1   Bronx   Co-op City  40.874294 -73.829939
2   Bronx  Eastchester  40.887556 -73.827806
3   Bronx    Fieldston  40.895437 -73.905643
4   Bronx    Riverdale  40.890834 -73.912585

In [8]:
address = 'New York City, NY'

geolocator = Nominatim(user_agent="ny_explorer")
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
print('The geograpical coordinate of New York City are {}, {}.'.format(latitude, longitude))

The geograpical coordinate of New York City are 40.7127281, -74.0060152.


In [9]:
# create map of New York using latitude and longitude values
map_newyork = folium.Map(location=[latitude, longitude], zoom_start=10)

# add markers to map
for lat, lng, borough, neighborhood in zip(neighborhoods['Latitude'], neighborhoods['Longitude'], neighborhoods['Borough'], neighborhoods['Neighborhood']):
    label = '{}, {}'.format(neighborhood, borough)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_newyork)  
    
map_newyork

In [10]:
manhattan_data = neighborhoods[neighborhoods['Borough'] == 'Manhattan'].reset_index(drop=True)
manhattan_data.head()


Borough        Neighborhood   Latitude  Longitude
0  Manhattan         Marble Hill  40.876551 -73.910660
1  Manhattan           Chinatown  40.715618 -73.994279
2  Manhattan  Washington Heights  40.851903 -73.936900
3  Manhattan              Inwood  40.867684 -73.921210
4  Manhattan    Hamilton Heights  40.823604 -73.949688

In [11]:
bx_data = neighborhoods[neighborhoods['Borough'] == 'Bronx'].reset_index(drop=True)
bx_data.head()

Borough Neighborhood   Latitude  Longitude
0   Bronx    Wakefield  40.894705 -73.847201
1   Bronx   Co-op City  40.874294 -73.829939
2   Bronx  Eastchester  40.887556 -73.827806
3   Bronx    Fieldston  40.895437 -73.905643
4   Bronx    Riverdale  40.890834 -73.912585

In [12]:
q_data = neighborhoods[neighborhoods['Borough'] == 'Queens'].reset_index(drop=True)
q_data.head()

Borough     Neighborhood   Latitude  Longitude
0  Queens          Astoria  40.768509 -73.915654
1  Queens         Woodside  40.746349 -73.901842
2  Queens  Jackson Heights  40.751981 -73.882821
3  Queens         Elmhurst  40.744049 -73.881656
4  Queens     Howard Beach  40.654225 -73.838138

In [13]:
s_data = neighborhoods[neighborhoods['Borough'] == 'Staten Island'].reset_index(drop=True)
s_data.head()

Borough   Neighborhood   Latitude  Longitude
0  Staten Island     St. George  40.644982 -74.079353
1  Staten Island   New Brighton  40.640615 -74.087017
2  Staten Island      Stapleton  40.626928 -74.077902
3  Staten Island       Rosebank  40.615305 -74.069805
4  Staten Island  West Brighton  40.631879 -74.107182

In [14]:
address_man = 'Manhattan, NY'

geolocator = Nominatim(user_agent="ny_explorer")
location_man = geolocator.geocode(address_man)
latitude_man = location_man.latitude
longitude_man = location_man.longitude
print('The geograpical coordinate of Manhattan are {}, {}.'.format(latitude_man, longitude_man))

The geograpical coordinate of Manhattan are 40.7896239, -73.9598939.


In [15]:
br_data = neighborhoods[neighborhoods['Borough'] == 'Brooklyn'].reset_index(drop=True)
br_data.head()

Borough Neighborhood   Latitude  Longitude
0  Brooklyn    Bay Ridge  40.625801 -74.030621
1  Brooklyn  Bensonhurst  40.611009 -73.995180
2  Brooklyn  Sunset Park  40.645103 -74.010316
3  Brooklyn   Greenpoint  40.730201 -73.954241
4  Brooklyn    Gravesend  40.595260 -73.973471

In [16]:
address_bx = 'Bronx, NY'

geolocator = Nominatim(user_agent="ny_explorer")
location_bx = geolocator.geocode(address_bx)
latitude_bx = location_bx.latitude
longitude_bx = location_bx.longitude
print('The geograpical coordinate of Bronx are {}, {}.'.format(latitude_bx, longitude_bx))

The geograpical coordinate of Bronx are 40.8466508, -73.8785937.


In [17]:
address_br = 'Brooklyn, NY'

geolocator = Nominatim(user_agent="ny_explorer")
location_br = geolocator.geocode(address_br)
latitude_br = location_br.latitude
longitude_br = location_br.longitude
print('The geograpical coordinate of Brooklyn are {}, {}.'.format(latitude_br, longitude_br))

The geograpical coordinate of Brooklyn are 40.6501024, -73.9495829.


In [18]:
address_q = 'Queens, NY'

geolocator = Nominatim(user_agent="ny_explorer")
location_q = geolocator.geocode(address_q)
latitude_q = location_q.latitude
longitude_q = location_q.longitude
print('The geograpical coordinate of Queens are {}, {}.'.format(latitude_q, longitude_q))

The geograpical coordinate of Queens are 40.7498243, -73.7976337.


In [19]:
address_s = 'Staten Island, NY'

geolocator = Nominatim(user_agent="ny_explorer")
location_s = geolocator.geocode(address_s)
latitude_s = location_s.latitude
longitude_s = location_s.longitude
print('The geograpical coordinate of Staten Island are {}, {}.'.format(latitude_s, longitude_s))

The geograpical coordinate of Staten Island are 40.5834557, -74.1496048.


In [20]:
# create map of Manhattan using latitude and longitude values
map_manhattan = folium.Map(location=[latitude, longitude], zoom_start=11)

# add markers to map
for lat, lng, label in zip(manhattan_data['Latitude'], manhattan_data['Longitude'], manhattan_data['Neighborhood']):
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_manhattan)  
    
map_manhattan

In [21]:
map_br = folium.Map(location=[latitude, longitude], zoom_start=11)

# add markers to map
for lat, lng, label in zip(br_data['Latitude'], br_data['Longitude'], br_data['Neighborhood']):
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_br)  
    
map_br

In [22]:
map_q = folium.Map(location=[latitude, longitude], zoom_start=11)

# add markers to map
for lat, lng, label in zip(q_data['Latitude'], q_data['Longitude'], q_data['Neighborhood']):
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_q)  
    
map_q

In [23]:
map_s = folium.Map(location=[latitude, longitude], zoom_start=11)

# add markers to map
for lat, lng, label in zip(s_data['Latitude'], s_data['Longitude'], s_data['Neighborhood']):
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_s)  
    
map_s

In [24]:
map_bx = folium.Map(location=[latitude, longitude], zoom_start=11)

# add markers to map
for lat, lng, label in zip(bx_data['Latitude'], bx_data['Longitude'], bx_data['Neighborhood']):
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_bx)  
    
map_bx

In [25]:
CLIENT_ID = 'HBZINFTZDZDIPKAXYWARSTHBS5XOJFVMZTSQCCVD0GQPJ4UF' # your Foursquare ID
CLIENT_SECRET = 'PR4EAL1B5PLXB2UZFGITS2EBYDQF5UD0YUPJZK5032HU03RK' # your Foursquare Secret
VERSION = '20180605' # Foursquare API version
LIMIT = 100 # A default Foursquare API limit value

print('Your credentails:')
print('CLIENT_ID: ' + CLIENT_ID)
print('CLIENT_SECRET:' + CLIENT_SECRET)

Your credentails:
CLIENT_ID: HBZINFTZDZDIPKAXYWARSTHBS5XOJFVMZTSQCCVD0GQPJ4UF
CLIENT_SECRET:PR4EAL1B5PLXB2UZFGITS2EBYDQF5UD0YUPJZK5032HU03RK


In [26]:
def getNearbyVenues(names, latitudes, longitudes, radius=500):
    
    venues_list=[]
    for name, lat, lng in zip(names, latitudes, longitudes):
        print(name)
            
        # create the API request URL
        url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            lat, 
            lng, 
            radius, 
            LIMIT)
            
        # make the GET request
        results = requests.get(url).json()["response"]['groups'][0]['items']
        
        # return only relevant information for each nearby venue
        venues_list.append([(
            name, 
            lat, 
            lng, 
            v['venue']['name'], 
            v['venue']['location']['lat'], 
            v['venue']['location']['lng'],  
            v['venue']['categories'][0]['name']) for v in results])

    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['Neighborhood', 
                  'Neighborhood Latitude', 
                  'Neighborhood Longitude', 
                  'Venue', 
                  'Venue Latitude', 
                  'Venue Longitude', 
                  'Venue Category']
    
    return(nearby_venues)

In [27]:
manhattan_venues = getNearbyVenues(names=manhattan_data['Neighborhood'],
                                   latitudes=manhattan_data['Latitude'],
                                   longitudes=manhattan_data['Longitude']
                                  )

Marble Hill
Chinatown
Washington Heights
Inwood
Hamilton Heights
Manhattanville
Central Harlem
East Harlem
Upper East Side
Yorkville
Lenox Hill
Roosevelt Island
Upper West Side
Lincoln Square
Clinton
Midtown
Murray Hill
Chelsea
Greenwich Village
East Village
Lower East Side
Tribeca
Little Italy
Soho
West Village
Manhattan Valley
Morningside Heights
Gramercy
Battery Park City
Financial District
Carnegie Hill
Noho
Civic Center
Midtown South
Sutton Place
Turtle Bay
Tudor City
Stuyvesant Town
Flatiron
Hudson Yards


In [29]:
br_venues = getNearbyVenues(names=br_data['Neighborhood'],
                                   latitudes=br_data['Latitude'],
                                   longitudes=br_data['Longitude']
                                  )

Bay Ridge
Bensonhurst
Sunset Park
Greenpoint
Gravesend
Brighton Beach
Sheepshead Bay
Manhattan Terrace
Flatbush
Crown Heights
East Flatbush
Kensington
Windsor Terrace
Prospect Heights
Brownsville
Williamsburg
Bushwick
Bedford Stuyvesant
Brooklyn Heights
Cobble Hill
Carroll Gardens
Red Hook
Gowanus
Fort Greene
Park Slope
Cypress Hills
East New York
Starrett City
Canarsie
Flatlands
Mill Island
Manhattan Beach
Coney Island
Bath Beach
Borough Park
Dyker Heights
Gerritsen Beach
Marine Park
Clinton Hill
Sea Gate
Downtown
Boerum Hill
Prospect Lefferts Gardens
Ocean Hill
City Line
Bergen Beach
Midwood
Prospect Park South
Georgetown
East Williamsburg
North Side
South Side
Ocean Parkway
Fort Hamilton
Ditmas Park
Wingate
Rugby
Remsen Village
New Lots
Paerdegat Basin
Mill Basin
Fulton Ferry
Vinegar Hill
Weeksville
Broadway Junction
Dumbo
Homecrest
Highland Park
Madison
Erasmus


In [30]:
q_venues = getNearbyVenues(names=q_data['Neighborhood'],
                                   latitudes=q_data['Latitude'],
                                   longitudes=q_data['Longitude']
                                  )

Astoria
Woodside
Jackson Heights
Elmhurst
Howard Beach
Corona
Forest Hills
Kew Gardens
Richmond Hill
Flushing
Long Island City
Sunnyside
East Elmhurst
Maspeth
Ridgewood
Glendale
Rego Park
Woodhaven
Ozone Park
South Ozone Park
College Point
Whitestone
Bayside
Auburndale
Little Neck
Douglaston
Glen Oaks
Bellerose
Kew Gardens Hills
Fresh Meadows
Briarwood
Jamaica Center
Oakland Gardens
Queens Village
Hollis
South Jamaica
St. Albans
Rochdale
Springfield Gardens
Cambria Heights
Rosedale
Far Rockaway
Broad Channel
Breezy Point
Steinway
Beechhurst
Bay Terrace
Edgemere
Arverne
Rockaway Beach
Neponsit
Murray Hill
Floral Park
Holliswood
Jamaica Estates
Queensboro Hill
Hillcrest
Ravenswood
Lindenwood
Laurelton
Lefrak City
Belle Harbor
Rockaway Park
Somerville
Brookville
Bellaire
North Corona
Forest Hills Gardens
Jamaica Hills
Utopia
Pomonok
Astoria Heights
Hunters Point
Sunnyside Gardens
Blissville
Roxbury
Middle Village
Malba
Hammels
Bayswater
Queensbridge


In [31]:
s_venues = getNearbyVenues(names=s_data['Neighborhood'],
                                   latitudes=s_data['Latitude'],
                                   longitudes=s_data['Longitude']
                                  )

St. George
New Brighton
Stapleton
Rosebank
West Brighton
Grymes Hill
Todt Hill
South Beach
Port Richmond
Mariner's Harbor
Port Ivory
Castleton Corners
New Springville
Travis
New Dorp
Oakwood
Great Kills
Eltingville
Annadale
Woodrow
Tottenville
Tompkinsville
Silver Lake
Sunnyside
Park Hill
Westerleigh
Graniteville
Arlington
Arrochar
Grasmere
Old Town
Dongan Hills
Midland Beach
Grant City
New Dorp Beach
Bay Terrace
Huguenot
Pleasant Plains
Butler Manor
Charleston
Rossville
Arden Heights
Greenridge
Heartland Village
Chelsea
Bloomfield
Bulls Head
Richmond Town
Shore Acres
Clifton
Concord
Emerson Hill
Randall Manor
Howland Hook
Elm Park
Manor Heights
Willowbrook
Sandy Ground
Egbertville
Prince's Bay
Lighthouse Hill
Richmond Valley
Fox Hills


In [32]:
bx_venues = getNearbyVenues(names=bx_data['Neighborhood'],
                                   latitudes=bx_data['Latitude'],
                                   longitudes=bx_data['Longitude']
                                  )

Wakefield
Co-op City
Eastchester
Fieldston
Riverdale
Kingsbridge
Woodlawn
Norwood
Williamsbridge
Baychester
Pelham Parkway
City Island
Bedford Park
University Heights
Morris Heights
Fordham
East Tremont
West Farms
High  Bridge
Melrose
Mott Haven
Port Morris
Longwood
Hunts Point
Morrisania
Soundview
Clason Point
Throgs Neck
Country Club
Parkchester
Westchester Square
Van Nest
Morris Park
Belmont
Spuyten Duyvil
North Riverdale
Pelham Bay
Schuylerville
Edgewater Park
Castle Hill
Olinville
Pelham Gardens
Concourse
Unionport
Edenwald
Claremont Village
Concourse Village
Mount Eden
Mount Hope
Bronxdale
Allerton
Kingsbridge Heights


In [33]:
print('Manhattan: There are {} uniques categories.'.format(len(manhattan_venues['Venue Category'].unique())))
print('Brooklyn: There are {} uniques categories.'.format(len(br_venues['Venue Category'].unique())))
print('Queens: There are {} uniques categories.'.format(len(q_venues['Venue Category'].unique())))
print('Staten Island: There are {} uniques categories.'.format(len(s_venues['Venue Category'].unique())))
print('Bronx: There are {} uniques categories.'.format(len(bx_venues['Venue Category'].unique())))



Manhattan: There are 331 uniques categories.
Brooklyn: There are 293 uniques categories.
Queens: There are 265 uniques categories.
Staten Island: There are 181 uniques categories.
Bronx: There are 168 uniques categories.


In [34]:
#Manhattan
m_onehot = pd.get_dummies(manhattan_venues[['Venue Category']], prefix="", prefix_sep="")
# add neighborhood column back to dataframe
m_onehot['Neighborhood'] = manhattan_venues['Neighborhood'] 
# move neighborhood column to the first column
mfixed_columns = [m_onehot.columns[-1]] + list(m_onehot.columns[:-1])
m_onehot = m_onehot[mfixed_columns]
m_onehot.head()

Neighborhood  Accessories Store  Adult Boutique  Afghan Restaurant  \
0  Marble Hill                  0               0                  0   
1  Marble Hill                  0               0                  0   
2  Marble Hill                  0               0                  0   
3  Marble Hill                  0               0                  0   
4  Marble Hill                  0               0                  0   

   African Restaurant  American Restaurant  Animal Shelter  Antique Shop  \
0                   0                    0               0             0   
1                   0                    0               0             0   
2                   0                    0               0             0   
3                   0                    0               0             0   
4                   0                    0               0             0   

   Arepa Restaurant  Argentinian Restaurant  Art Gallery  Art Museum  \
0                 0                       0            0           0   
1                 0                       0            0           0   
2                 0                       0            0           0   
3                 0                       0            0           0   
4                 0                       0            0           0   

   Arts & Crafts Store  Asian Restaurant  Athletics & Sports  Auditorium  \
0                    0                 0                   0           0   
1                    0                 0                   0           0   
2                    0                 0                   0           0   
3                    0                 0                   0           0   
4                    0                 0                   0           0   

   Australian Restaurant  Austrian Restaurant  Auto Workshop  BBQ Joint  \
0                      0                    0              0          0   
1                      0                    0              0          0   
2                      0                    0              0          0   
3                      0                    0              0          0   
4                      0                    0              0          0   

   Baby Store  Bagel Shop  Bakery  Bank  Bar  Baseball Field  \
0           0           0       0     0    0               0   
1           0           0       0     0    0               0   
2           0           0       0     0    0               0   
3           0           0       0     0    0               0   
4           0           0       0     0    0               0   

   Basketball Court  Bed & Breakfast  Beer Bar  Beer Garden  Beer Store  \
0                 0                0         0            0           0   
1                 0                0         0            0           0   
2                 0                0         0            0           0   
3                 0                0         0            0           0   
4                 0                0         0            0           0   

   Big Box Store  Bike Rental / Bike Share  Bike Shop  Bike Trail  Bistro  \
0              0                         0          0           0       0   
1              0                         0          0           0       0   
2              0                         0          0           0       0   
3              0                         0          0           0       0   
4              0                         0          0           0       0   

   Board Shop  Boat or Ferry  Bookstore  Boutique  Boxing Gym  \
0           0              0          0         0           0   
1           0              0          0         0           0   
2           0              0          0         0           0   
3           0              0          0         0           0   
4           0              0          0         0           0   

   Brazilian Restaurant  Breakfast Spot  Bridal Shop  Bridge  Bubble Tea Shop  \


In [35]:
#Brooklyn
br_onehot = pd.get_dummies(br_venues[['Venue Category']], prefix="", prefix_sep="")
# add neighborhood column back to dataframe
br_onehot['Neighborhood'] = br_venues['Neighborhood'] 
# move neighborhood column to the first column
brfixed_columns = [br_onehot.columns[-1]] + list(br_onehot.columns[:-1])
br_onehot = br_onehot[brfixed_columns]
br_onehot.head()

Yoga Studio  Accessories Store  Adult Boutique  African Restaurant  \
0            0                  0               0                   0   
1            0                  0               0                   0   
2            0                  0               0                   0   
3            0                  0               0                   0   
4            0                  0               0                   0   

   American Restaurant  Antique Shop  Arepa Restaurant  \
0                    0             0                 0   
1                    0             0                 0   
2                    0             0                 0   
3                    0             0                 0   
4                    0             0                 0   

   Argentinian Restaurant  Art Gallery  Arts & Crafts Store  \
0                       0            0                    0   
1                       0            0                    0   
2                       0            0                    0   
3                       0            0                    0   
4                       0            0                    0   

   Arts & Entertainment  Asian Restaurant  Athletics & Sports  BBQ Joint  \
0                     0                 0                   0          0   
1                     0                 0                   0          0   
2                     0                 0                   0          0   
3                     0                 0                   0          0   
4                     0                 0                   0          0   

   Bagel Shop  Bakery  Bank  Bar  Baseball Field  Baseball Stadium  \
0           0       0     0    0               0                 0   
1           1       0     0    0               0                 0   
2           0       0     0    0               0                 0   
3           0       0     0    0               0                 0   
4           0       0     0    0               0                 0   

   Basketball Court  Beach  Beer Bar  Beer Garden  Beer Store  Big Box Store  \
0                 0      0         0            0           0              0   
1                 0      0         0            0           0              0   
2                 0      0         0            0           0              0   
3                 0      0         0            0           0              0   
4                 0      0         0            0           0              0   

   Bike Rental / Bike Share  Bike Shop  Bike Trail  Bistro  Board Shop  \
0                         0          0           0       0           0   
1                         0          0           0       0           0   
2                         0          0           0       0           0   
3                         0          0           0       0           0   
4                         0          0           0       0           0   

   Boat or Ferry  Bookstore  Boutique  Boxing Gym  Brazilian Restaurant  \
0              0          0         0           0                     0   
1              0          0         0           0                     0   
2              0          0         0           0                     0   
3              0          0         0           0                     0   
4              0          0         0           0                     0   

   Breakfast Spot  Brewery  Bridge  Bubble Tea Shop  Buffet  Burger Joint  \
0               0        0       0                0       0             0   
1               0        0       0                0       0             0   
2               0        0       0                0       0             0   
3               0        0       0                0       0             0   
4               1        0       0                0       0             0   

   Burmese Restaurant  Burrito Place  Bus Line  Bus Station  Bus Stop  \
0                   0              0         

In [36]:
#Queens
q_onehot = pd.get_dummies(q_venues[['Venue Category']], prefix="", prefix_sep="")
# add neighborhood column back to dataframe
q_onehot['Neighborhood'] = q_venues['Neighborhood'] 
# move neighborhood column to the first column
qfixed_columns = [q_onehot.columns[-1]] + list(q_onehot.columns[:-1])
q_onehot = q_onehot[qfixed_columns]
q_onehot.head()

Yoga Studio  Accessories Store  Afghan Restaurant  American Restaurant  \
0            0                  0                  0                    0   
1            0                  0                  0                    0   
2            0                  0                  0                    0   
3            0                  0                  0                    0   
4            0                  0                  0                    0   

   Arepa Restaurant  Argentinian Restaurant  Art Gallery  Art Museum  \
0                 0                       0            0           0   
1                 0                       0            0           0   
2                 0                       0            0           0   
3                 0                       0            0           0   
4                 0                       0            0           0   

   Arts & Crafts Store  Arts & Entertainment  Asian Restaurant  \
0                    0                     0                 0   
1                    0                     0                 0   
2                    0                     0                 0   
3                    0                     0                 0   
4                    0                     0                 0   

   Athletics & Sports  Automotive Shop  BBQ Joint  Bagel Shop  Bakery  Bank  \
0                   0                0          0           0       0     0   
1                   0                0          0           0       0     0   
2                   0                0          0           0       0     0   
3                   0                0          0           0       0     0   
4                   0                0          0           0       0     0   

   Bar  Baseball Field  Basketball Court  Bath House  Beach  Beach Bar  \
0    0               0                 0           0      0          0   
1    0               0                 0           0      0          0   
2    0               0                 0           0      0          0   
3    0               0                 0           0      0          0   
4    0               0                 0           0      0          0   

   Beer Garden  Bike Trail  Bistro  Board Shop  Bookstore  Boutique  \
0            0           0       0           0          0         0   
1            0           0       0           0          0         0   
2            0           0       0           0          0         0   
3            0           0       0           0          0         0   
4            0           0       0           0          0         0   

   Bowling Alley  Boxing Gym  Brazilian Restaurant  Breakfast Spot  Brewery  \
0              0           0                     1               0        0   
1              0           0                     0               0        0   
2              0           0                     0               0        0   
3              0           0                     0               0        0   
4              0           0                     0               0        0   

   Bubble Tea Shop  Buffet  Building  Burger Joint  Burrito Place  Bus Line  \
0                0       0         0             0              0         0   
1                0       0         0             0              0         0   
2                0       0         0             0              0         0   
3                0       0         0             0              0         0   
4                0       0         0             0              0         0   

   Bus Station  Bus Stop  Business Service  Butcher  Cafeteria  Café  \
0            0         0                 0        0          0     0   
1            0         0                 0        0          0     0   
2            0         0                 0        0          0     0   
3            0         0                 0        0          0     0   
4            0         0                 0        0  

In [37]:
#Staten Island
s_onehot = pd.get_dummies(s_venues[['Venue Category']], prefix="", prefix_sep="")
# add neighborhood column back to dataframe
s_onehot['Neighborhood'] = s_venues['Neighborhood'] 
# move neighborhood column to the first column
sfixed_columns = [s_onehot.columns[-1]] + list(s_onehot.columns[:-1])
s_onehot = s_onehot[sfixed_columns]
s_onehot.head()

Neighborhood  American Restaurant  Arcade  Art Gallery  Art Museum  \
0   St. George                    0       0            0           0   
1   St. George                    0       0            0           0   
2   St. George                    0       0            0           0   
3   St. George                    0       0            0           0   
4   St. George                    0       0            0           0   

   Arts & Crafts Store  Asian Restaurant  Athletics & Sports  BBQ Joint  \
0                    0                 0                   0          0   
1                    0                 0                   0          0   
2                    0                 0                   0          0   
3                    0                 0                   0          0   
4                    0                 0                   0          0   

   Bagel Shop  Bakery  Bank  Bar  Baseball Field  Baseball Stadium  \
0           0       0     0    0               0                 0   
1           0       0     0    0               0                 0   
2           0       0     0    0               0                 0   
3           0       0     0    0               0                 1   
4           0       0     0    0               0                 0   

   Basketball Court  Beach  Beer Bar  Big Box Store  Board Shop  \
0                 0      0         0              0           0   
1                 0      0         0              0           0   
2                 0      0         0              0           0   
3                 0      0         0              0           0   
4                 0      0         0              0           0   

   Boat or Ferry  Bookstore  Bowling Alley  Breakfast Spot  Brewery  \
0              0          0              0               0        0   
1              0          0              0               0        0   
2              0          0              0               0        0   
3              0          0              0               0        0   
4              0          0              0               0        0   

   Bridal Shop  Bubble Tea Shop  Burger Joint  Bus Station  Bus Stop  Butcher  \
0            0                0             0            0         0        0   
1            0                0             0            0         0        0   
2            0                0             0            0         0        0   
3            0                0             0            0         0        0   
4            0                0             1            0         0        0   

   Café  Cajun / Creole Restaurant  Campground  Caribbean Restaurant  \
0     0                          0           0                     0   
1     0                          0           0                     0   
2     0                          0           0                     0   
3     0                          0           0                     0   
4     0                          0           0                     0   

   Check Cashing Service  Chinese Restaurant  Clothing Store  Coffee Shop  \
0                      0                   0               0            0   
1                      0                   0               0            0   
2                      0                   0               0            0   
3                      0                   0               0            0   
4                      0                   0               0            0   

   Comedy Club  Concert Hall  Construction & Landscaping  Convenience Store  \
0            0             0                           0                  0   
1            0             0                           0                  0   
2            0             0                           0                  0   
3            0             0                           0                  0   
4            0             0                           0                  0   

   Cosmet

In [38]:
#Bronx
bx_onehot = pd.get_dummies(bx_venues[['Venue Category']], prefix="", prefix_sep="")
# add neighborhood column back to dataframe
bx_onehot['Neighborhood'] = bx_venues['Neighborhood'] 
# move neighborhood column to the first column
bxfixed_columns = [bx_onehot.columns[-1]] + list(bx_onehot.columns[:-1])
bx_onehot = bx_onehot[bxfixed_columns]
bx_onehot.head()

Neighborhood  Accessories Store  African Restaurant  American Restaurant  \
0    Wakefield                  0                   0                    0   
1    Wakefield                  0                   0                    0   
2    Wakefield                  0                   0                    0   
3    Wakefield                  0                   0                    0   
4    Wakefield                  0                   0                    0   

   Arcade  Arepa Restaurant  Art Gallery  Art Museum  Arts & Crafts Store  \
0       0                 0            0           0                    0   
1       0                 0            0           0                    0   
2       0                 0            0           0                    0   
3       0                 0            0           0                    0   
4       0                 0            0           0                    0   

   Asian Restaurant  Athletics & Sports  BBQ Joint  Bagel Shop  Bakery  Bank  \
0                 0                   0          0           0       0     0   
1                 0                   0          0           0       0     0   
2                 0                   0          0           0       0     0   
3                 0                   0          0           0       0     0   
4                 0                   0          0           0       0     0   

   Bar  Baseball Field  Basketball Court  Beer Bar  Boat or Ferry  Bookstore  \
0    0               0                 0         0              0          0   
1    0               0                 0         0              0          0   
2    0               0                 0         0              0          0   
3    0               0                 0         0              0          0   
4    0               0                 0         0              0          0   

   Bowling Alley  Breakfast Spot  Brewery  Buffet  Building  Burger Joint  \
0              0               0        0       0         0             0   
1              0               0        0       0         0             0   
2              0               0        0       0         0             0   
3              0               0        0       0         0             0   
4              0               0        0       0         0             0   

   Bus Line  Bus Station  Bus Stop  Café  Candy Store  Caribbean Restaurant  \
0         0            0         0     0            0                     0   
1         0            0         0     0            0                     0   
2         0            0         0     0            0                     0   
3         0            0         0     0            0                     0   
4         0            0         0     0            0                     0   

   Check Cashing Service  Cheese Shop  Chinese Restaurant  Clothing Store  \
0                      0            0                   0               0   
1                      0            0                   0               0   
2                      0            0                   0               0   
3                      0            0                   0               0   
4                      0            0                   0               0   

   Coffee Shop  Comfort Food Restaurant  Convenience Store  Cosmetics Shop  \
0            0                        0                  0               0   
1            0                        0                  0               0   
2            0                        0                  0               0   
3            0                        0                  0               0   
4            0                        0                  0               0   

   Cuban Restaurant  Dance Studio  Deli / Bodega  Department Store  \
0                 0             0              0                 0   
1                 0             0              0                 0   
2                 0         

In [39]:
m_grouped = m_onehot.groupby('Neighborhood').mean().reset_index()
m_grouped

Neighborhood  Accessories Store  Adult Boutique  Afghan Restaurant  \
0     Battery Park City           0.000000        0.000000               0.00   
1         Carnegie Hill           0.000000        0.000000               0.00   
2        Central Harlem           0.000000        0.000000               0.00   
3               Chelsea           0.000000        0.000000               0.00   
4             Chinatown           0.000000        0.000000               0.00   
5          Civic Center           0.000000        0.000000               0.00   
6               Clinton           0.000000        0.000000               0.00   
7           East Harlem           0.000000        0.000000               0.00   
8          East Village           0.000000        0.000000               0.00   
9    Financial District           0.000000        0.000000               0.00   
10             Flatiron           0.000000        0.000000               0.00   
11             Gramercy           0.000000        0.000000               0.00   
12    Greenwich Village           0.020000        0.000000               0.00   
13     Hamilton Heights           0.000000        0.015873               0.00   
14         Hudson Yards           0.000000        0.000000               0.00   
15               Inwood           0.000000        0.000000               0.00   
16           Lenox Hill           0.000000        0.000000               0.01   
17       Lincoln Square           0.000000        0.000000               0.00   
18         Little Italy           0.000000        0.000000               0.00   
19      Lower East Side           0.000000        0.000000               0.00   
20     Manhattan Valley           0.000000        0.000000               0.00   
21       Manhattanville           0.000000        0.000000               0.00   
22          Marble Hill           0.000000        0.000000               0.00   
23              Midtown           0.000000        0.000000               0.00   
24        Midtown South           0.000000        0.000000               0.00   
25  Morningside Heights           0.000000        0.000000               0.00   
26          Murray Hill           0.000000        0.000000               0.00   
27                 Noho           0.000000        0.000000               0.00   
28     Roosevelt Island           0.000000        0.000000               0.00   
29                 Soho           0.000000        0.000000               0.00   
30      Stuyvesant Town           0.000000        0.000000               0.00   
31         Sutton Place           0.000000        0.010000               0.00   
32              Tribeca           0.000000        0.000000               0.00   
33           Tudor City           0.000000        0.000000               0.00   
34           Turtle Bay           0.000000        0.000000               0.00   
35      Upper East Side           0.000000        0.000000               0.00   
36      Upper West Side           0.000000        0.000000               0.00   
37   Washington Heights           0.011765        0.000000               0.00   
38         West Village           0.010000        0.010000               0.00   
39            Yorkville           0.000000        0.000000               0.00   

    African Restaurant  American Restaurant  Animal Shelter  Antique Shop  \
0             0.000000             0.012658            0.00          0.00   
1             0.000000             0.010309            0.00          0.00   
2             0.046512             0.046512            0.00          0.00   
3             0.000000             0.040000            0.00          0.00   
4             0.000000             0.040000            0.00          0.00   
5             0.000000             0.030000            0.00          0.01   
6             0.000000             0.040000            0.00          0.00   
7             0.000000             0.000000            0.00          0.00

In [40]:
br_grouped = br_onehot.groupby('Neighborhood').mean().reset_index()
br_grouped

Neighborhood  Yoga Studio  Accessories Store  Adult Boutique  \
0                  Bath Beach     0.000000           0.000000            0.00   
1                   Bay Ridge     0.000000           0.000000            0.00   
2          Bedford Stuyvesant     0.000000           0.000000            0.00   
3                 Bensonhurst     0.000000           0.000000            0.00   
4                Bergen Beach     0.000000           0.000000            0.00   
5                 Boerum Hill     0.022472           0.000000            0.00   
6                Borough Park     0.000000           0.000000            0.00   
7              Brighton Beach     0.000000           0.000000            0.00   
8           Broadway Junction     0.000000           0.000000            0.00   
9            Brooklyn Heights     0.040000           0.000000            0.00   
10                Brownsville     0.000000           0.000000            0.00   
11                   Bushwick     0.000000           0.000000            0.00   
12                   Canarsie     0.000000           0.000000            0.00   
13            Carroll Gardens     0.000000           0.000000            0.00   
14                  City Line     0.000000           0.000000            0.00   
15               Clinton Hill     0.032258           0.000000            0.00   
16                Cobble Hill     0.030612           0.000000            0.00   
17               Coney Island     0.000000           0.000000            0.00   
18              Crown Heights     0.000000           0.000000            0.00   
19              Cypress Hills     0.000000           0.000000            0.00   
20                Ditmas Park     0.019608           0.000000            0.00   
21                   Downtown     0.010000           0.000000            0.00   
22                      Dumbo     0.029851           0.000000            0.00   
23              Dyker Heights     0.000000           0.000000            0.00   
24              East Flatbush     0.000000           0.000000            0.00   
25              East New York     0.000000           0.000000            0.00   
26          East Williamsburg     0.000000           0.000000            0.00   
27                    Erasmus     0.047619           0.000000            0.00   
28                   Flatbush     0.000000           0.000000            0.00   
29                  Flatlands     0.000000           0.000000            0.00   
30                Fort Greene     0.015625           0.000000            0.00   
31              Fort Hamilton     0.000000           0.000000            0.00   
32               Fulton Ferry     0.000000           0.000000            0.00   
33                 Georgetown     0.000000           0.000000            0.00   
34            Gerritsen Beach     0.000000           0.000000            0.00   
35                    Gowanus     0.030303           0.000000            0.00   
36                  Gravesend     0.000000           0.000000            0.00   
37                 Greenpoint     0.030000           0.000000            0.00   
38              Highland Park     0.000000           0.000000            0.00   
39                  Homecrest     0.000000           0.000000            0.00   
40                 Kensington     0.000000           0.000000            0.00   
41                    Madison     0.000000           0.000000            0.00   
42            Manhattan Beach     0.000000           0.000000            0.00   
43          Manhattan Terrace     0.000000           0.000000            0.00   
44                Marine Park     0.000000           0.000000            0.00   
45                    Midwood     0.000000           0.000000            0.00   
46                 Mill Basin     0.000000           0.000000            0.00   
47                Mill Island     0.000000           0.000000            0.00   
48                   New Lots     0.000000      

In [41]:
q_grouped = q_onehot.groupby('Neighborhood').mean().reset_index()
q_grouped

Neighborhood  Yoga Studio  Accessories Store  Afghan Restaurant  \
0                Arverne     0.000000           0.000000           0.000000   
1                Astoria     0.000000           0.000000           0.000000   
2        Astoria Heights     0.000000           0.000000           0.000000   
3             Auburndale     0.000000           0.000000           0.000000   
4            Bay Terrace     0.000000           0.027027           0.000000   
5                Bayside     0.014286           0.000000           0.000000   
6              Bayswater     0.000000           0.000000           0.000000   
7             Beechhurst     0.066667           0.000000           0.000000   
8               Bellaire     0.000000           0.000000           0.000000   
9           Belle Harbor     0.000000           0.000000           0.000000   
10             Bellerose     0.000000           0.000000           0.000000   
11            Blissville     0.000000           0.000000           0.000000   
12          Breezy Point     0.000000           0.000000           0.000000   
13             Briarwood     0.000000           0.000000           0.000000   
14         Broad Channel     0.000000           0.000000           0.000000   
15            Brookville     0.000000           0.000000           0.000000   
16       Cambria Heights     0.000000           0.000000           0.000000   
17         College Point     0.000000           0.000000           0.000000   
18                Corona     0.000000           0.000000           0.000000   
19            Douglaston     0.043478           0.000000           0.000000   
20         East Elmhurst     0.000000           0.000000           0.000000   
21              Edgemere     0.000000           0.000000           0.000000   
22              Elmhurst     0.000000           0.000000           0.000000   
23          Far Rockaway     0.000000           0.000000           0.000000   
24           Floral Park     0.000000           0.000000           0.000000   
25              Flushing     0.015873           0.000000           0.000000   
26          Forest Hills     0.051282           0.000000           0.000000   
27  Forest Hills Gardens     0.000000           0.000000           0.000000   
28         Fresh Meadows     0.000000           0.000000           0.000000   
29             Glen Oaks     0.000000           0.000000           0.000000   
30              Glendale     0.000000           0.000000           0.000000   
31               Hammels     0.000000           0.000000           0.000000   
32             Hillcrest     0.000000           0.000000           0.000000   
33                Hollis     0.000000           0.000000           0.000000   
34            Holliswood     0.000000           0.000000           0.000000   
35          Howard Beach     0.000000           0.000000           0.000000   
36         Hunters Point     0.014706           0.000000           0.000000   
37       Jackson Heights     0.000000           0.000000           0.000000   
38        Jamaica Center     0.000000           0.000000           0.000000   
39       Jamaica Estates     0.000000           0.000000           0.000000   
40         Jamaica Hills     0.000000           0.000000           0.000000   
41           Kew Gardens     0.000000           0.000000           0.000000   
42     Kew Gardens Hills     0.000000           0.000000           0.000000   
43             Laurelton     0.000000           0.000000           0.000000   
44           Lefrak City     0.000000           0.000000           0.000000   
45            Lindenwood     0.000000           0.000000           0.000000   
46           Little Neck     0.000000           0.000000           0.000000   
47      Long Island City     0.000000           0.000000           0.000000   
48                 Malba     0.000000           0.000000           0.000000   
49               Maspeth     0.000000           0.000000      

In [42]:
s_grouped = s_onehot.groupby('Neighborhood').mean().reset_index()
s_grouped

Neighborhood  American Restaurant    Arcade  Art Gallery  Art Museum  \
0            Annadale             0.000000  0.000000          0.0         0.0   
1       Arden Heights             0.000000  0.000000          0.0         0.0   
2           Arlington             0.000000  0.000000          0.0         0.0   
3            Arrochar             0.000000  0.000000          0.0         0.0   
4         Bay Terrace             0.000000  0.000000          0.0         0.0   
5          Bloomfield             0.000000  0.000000          0.0         0.0   
6          Bulls Head             0.022727  0.000000          0.0         0.0   
7        Butler Manor             0.000000  0.000000          0.0         0.0   
8   Castleton Corners             0.000000  0.000000          0.0         0.0   
9          Charleston             0.000000  0.000000          0.0         0.0   
10            Chelsea             0.000000  0.000000          0.0         0.0   
11            Clifton             0.000000  0.000000          0.0         0.0   
12            Concord             0.000000  0.000000          0.0         0.0   
13       Dongan Hills             0.000000  0.000000          0.0         0.0   
14        Egbertville             0.000000  0.000000          0.0         0.0   
15           Elm Park             0.125000  0.000000          0.0         0.0   
16        Eltingville             0.000000  0.000000          0.0         0.0   
17       Emerson Hill             0.000000  0.000000          0.0         0.0   
18          Fox Hills             0.000000  0.000000          0.0         0.0   
19       Graniteville             0.000000  0.000000          0.0         0.0   
20         Grant City             0.000000  0.000000          0.0         0.0   
21           Grasmere             0.000000  0.000000          0.0         0.0   
22        Great Kills             0.000000  0.000000          0.0         0.0   
23         Greenridge             0.000000  0.000000          0.0         0.0   
24        Grymes Hill             0.000000  0.000000          0.0         0.0   
25  Heartland Village             0.000000  0.000000          0.0         0.0   
26           Huguenot             0.000000  0.000000          0.0         0.0   
27    Lighthouse Hill             0.000000  0.000000          0.0         0.2   
28      Manor Heights             0.071429  0.000000          0.0         0.0   
29   Mariner's Harbor             0.000000  0.000000          0.0         0.0   
30      Midland Beach             0.000000  0.000000          0.0         0.0   
31       New Brighton             0.000000  0.000000          0.0         0.0   
32           New Dorp             0.000000  0.000000          0.0         0.0   
33     New Dorp Beach             0.000000  0.000000          0.0         0.0   
34    New Springville             0.000000  0.000000          0.0         0.0   
35            Oakwood             0.000000  0.000000          0.0         0.0   
36           Old Town             0.058824  0.000000          0.0         0.0   
37          Park Hill             0.000000  0.000000          0.0         0.0   
38    Pleasant Plains             0.000000  0.000000          0.0         0.0   
39      Port Richmond             0.000000  0.000000          0.0         0.0   
40       Prince's Bay             0.000000  0.000000          0.0         0.0   
41      Randall Manor             0.000000  0.000000          0.0         0.0   
42      Richmond Town             0.200000  0.000000          0.0         0.0   
43    Richmond Valley             0.000000  0.000000          0.0         0.0   
44           Rosebank             0.000000  0.000000          0.0         0.0   
45          Rossville             0.071429  0.000000          0.0         0.0   
46       Sandy Ground             0.000000  0.000000          0.1         0.0   
47        Shore Acres             0.000000  0.000000          0.0         0.0   
48        Silver Lake             0.2000

In [43]:
bx_grouped = bx_onehot.groupby('Neighborhood').mean().reset_index()
bx_grouped

Neighborhood  Accessories Store  African Restaurant  \
0              Allerton           0.000000            0.000000   
1            Baychester           0.000000            0.000000   
2          Bedford Park           0.000000            0.000000   
3               Belmont           0.000000            0.000000   
4             Bronxdale           0.000000            0.000000   
5           Castle Hill           0.000000            0.000000   
6           City Island           0.000000            0.000000   
7     Claremont Village           0.000000            0.000000   
8          Clason Point           0.000000            0.000000   
9            Co-op City           0.062500            0.000000   
10            Concourse           0.000000            0.000000   
11    Concourse Village           0.000000            0.000000   
12         Country Club           0.000000            0.000000   
13         East Tremont           0.000000            0.000000   
14          Eastchester           0.000000            0.000000   
15             Edenwald           0.000000            0.000000   
16       Edgewater Park           0.000000            0.000000   
17            Fieldston           0.000000            0.000000   
18              Fordham           0.011628            0.011628   
19         High  Bridge           0.000000            0.000000   
20          Hunts Point           0.000000            0.000000   
21          Kingsbridge           0.000000            0.000000   
22  Kingsbridge Heights           0.000000            0.000000   
23             Longwood           0.000000            0.000000   
24              Melrose           0.000000            0.000000   
25       Morris Heights           0.000000            0.000000   
26          Morris Park           0.000000            0.000000   
27           Morrisania           0.000000            0.000000   
28           Mott Haven           0.000000            0.000000   
29           Mount Eden           0.000000            0.000000   
30           Mount Hope           0.000000            0.000000   
31      North Riverdale           0.000000            0.000000   
32              Norwood           0.000000            0.000000   
33            Olinville           0.000000            0.000000   
34          Parkchester           0.000000            0.000000   
35           Pelham Bay           0.000000            0.000000   
36       Pelham Gardens           0.000000            0.000000   
37       Pelham Parkway           0.000000            0.000000   
38          Port Morris           0.000000            0.000000   
39            Riverdale           0.000000            0.000000   
40        Schuylerville           0.000000            0.000000   
41            Soundview           0.000000            0.000000   
42       Spuyten Duyvil           0.000000            0.000000   
43          Throgs Neck           0.000000            0.000000   
44            Unionport           0.000000            0.000000   
45   University Heights           0.000000            0.055556   
46             Van Nest           0.000000            0.000000   
47            Wakefield           0.000000            0.000000   
48           West Farms           0.000000            0.000000   
49   Westchester Square           0.000000            0.000000   
50       Williamsbridge           0.000000            0.000000   
51             Woodlawn           0.000000            0.000000   

    American Restaurant    Arcade  Arepa Restaurant  Art Gallery  Art Museum  \
0              0.000000  0.000000          0.000000     0.000000        0.00   
1              0.000000  0.045455          0.000000     0.000000        0.00   
2              0.000000  0.000000          0.000000     0.000000        0.00   
3              0.010000  0.000000          0.000000     0.000000        0.00   
4              0.000000  0.000000          0.000000     0.000000        0.00   
5              0.000000  0.00000

In [44]:
#Manhattan
num_top_venues = 5

for hood in m_grouped['Neighborhood']:
    print("----"+hood+"----")
    temp = m_grouped[m_grouped['Neighborhood'] == hood].T.reset_index()
    temp.columns = ['venue','freq']
    temp = temp.iloc[1:]
    temp['freq'] = temp['freq'].astype(float)
    temp = temp.round({'freq': 2})
    print(temp.sort_values('freq', ascending=False).reset_index(drop=True).head(num_top_venues))
    print('\n')

----Battery Park City----
           venue  freq
0           Park  0.08
1    Coffee Shop  0.06
2          Hotel  0.06
3  Boat or Ferry  0.04
4  Memorial Site  0.04


----Carnegie Hill----
         venue  freq
0  Coffee Shop  0.08
1         Café  0.05
2  Pizza Place  0.05
3    Wine Shop  0.04
4          Bar  0.04


----Central Harlem----
                  venue  freq
0    Seafood Restaurant  0.07
1    African Restaurant  0.05
2   American Restaurant  0.05
3  Gym / Fitness Center  0.05
4     French Restaurant  0.05


----Chelsea----
                 venue  freq
0          Coffee Shop  0.08
1               Bakery  0.05
2  American Restaurant  0.04
3          Art Gallery  0.04
4            Wine Shop  0.03


----Chinatown----
                 venue  freq
0   Chinese Restaurant  0.08
1               Bakery  0.07
2         Cocktail Bar  0.05
3  American Restaurant  0.04
4   Salon / Barbershop  0.03


----Civic Center----
                  venue  freq
0           Coffee Shop  0.07
1           

In [45]:
#Brooklyn
num_top_venues = 5

for hood in br_grouped['Neighborhood']:
    print("----"+hood+"----")
    temp = br_grouped[br_grouped['Neighborhood'] == hood].T.reset_index()
    temp.columns = ['venue','freq']
    temp = temp.iloc[1:]
    temp['freq'] = temp['freq'].astype(float)
    temp = temp.round({'freq': 2})
    print(temp.sort_values('freq', ascending=False).reset_index(drop=True).head(num_top_venues))
    print('\n')

----Bath Beach----
                venue  freq
0  Chinese Restaurant  0.07
1         Pizza Place  0.07
2         Gas Station  0.04
3  Italian Restaurant  0.04
4            Pharmacy  0.04


----Bay Ridge----
                venue  freq
0         Pizza Place  0.08
1                 Spa  0.06
2  Italian Restaurant  0.06
3                 Bar  0.04
4       Grocery Store  0.04


----Bedford Stuyvesant----
           venue  freq
0    Coffee Shop  0.11
1           Café  0.07
2    Pizza Place  0.07
3  Deli / Bodega  0.07
4            Bar  0.07


----Bensonhurst----
                venue  freq
0  Italian Restaurant  0.09
1  Chinese Restaurant  0.09
2          Donut Shop  0.06
3                Park  0.06
4    Sushi Restaurant  0.06


----Bergen Beach----
                venue  freq
0     Harbor / Marina  0.33
1                Park  0.17
2      Baseball Field  0.17
3          Playground  0.17
4  Athletics & Sports  0.17


----Boerum Hill----
                    venue  freq
0             Coffee Sh

In [46]:
#Queens
num_top_venues = 5

for hood in q_grouped['Neighborhood']:
    print("----"+hood+"----")
    temp = q_grouped[q_grouped['Neighborhood'] == hood].T.reset_index()
    temp.columns = ['venue','freq']
    temp = temp.iloc[1:]
    temp['freq'] = temp['freq'].astype(float)
    temp = temp.round({'freq': 2})
    print(temp.sort_values('freq', ascending=False).reset_index(drop=True).head(num_top_venues))
    print('\n')

----Arverne----
            venue  freq
0       Surf Spot  0.20
1  Sandwich Place  0.10
2   Metro Station  0.10
3        Bus Stop  0.05
4            Café  0.05


----Astoria----
                       venue  freq
0                        Bar  0.07
1  Middle Eastern Restaurant  0.06
2         Seafood Restaurant  0.04
3                     Bakery  0.04
4                       Café  0.03


----Astoria Heights----
                venue  freq
0  Italian Restaurant  0.13
1        Liquor Store  0.07
2              Bakery  0.07
3        Burger Joint  0.07
4              Museum  0.07


----Auburndale----
                venue  freq
0  Italian Restaurant  0.11
1           Pet Store  0.05
2          Hookah Bar  0.05
3                 Bar  0.05
4      Mattress Store  0.05


----Bay Terrace----
                 venue  freq
0       Clothing Store  0.11
1        Women's Store  0.05
2           Kids Store  0.05
3  American Restaurant  0.05
4           Shoe Store  0.05


----Bayside----
               

In [47]:
#Staten Island
num_top_venues = 5

for hood in s_grouped['Neighborhood']:
    print("----"+hood+"----")
    temp = s_grouped[s_grouped['Neighborhood'] == hood].T.reset_index()
    temp.columns = ['venue','freq']
    temp = temp.iloc[1:]
    temp['freq'] = temp['freq'].astype(float)
    temp = temp.round({'freq': 2})
    print(temp.sort_values('freq', ascending=False).reset_index(drop=True).head(num_top_venues))
    print('\n')

----Annadale----
            venue  freq
0     Pizza Place  0.22
1           Diner  0.11
2      Restaurant  0.11
3    Liquor Store  0.11
4  Cosmetics Shop  0.11


----Arden Heights----
                 venue  freq
0        Deli / Bodega  0.25
1             Pharmacy  0.25
2          Coffee Shop  0.25
3          Pizza Place  0.25
4  American Restaurant  0.00


----Arlington----
           venue  freq
0       Bus Stop   0.2
1  Deli / Bodega   0.2
2  Grocery Store   0.2
3  Boat or Ferry   0.2
4    Coffee Shop   0.2


----Arrochar----
                venue  freq
0  Italian Restaurant  0.09
1         Pizza Place  0.09
2          Bagel Shop  0.09
3       Deli / Bodega  0.09
4            Bus Stop  0.09


----Bay Terrace----
                venue  freq
0         Supermarket  0.25
1    Sushi Restaurant  0.12
2          Donut Shop  0.12
3  Salon / Barbershop  0.12
4      Shipping Store  0.12


----Bloomfield----
                 venue  freq
0           Theme Park  0.25
1         Burger Joint  0.2

In [48]:
#Bronx
num_top_venues = 5

for hood in bx_grouped['Neighborhood']:
    print("----"+hood+"----")
    temp = bx_grouped[bx_grouped['Neighborhood'] == hood].T.reset_index()
    temp.columns = ['venue','freq']
    temp = temp.iloc[1:]
    temp['freq'] = temp['freq'].astype(float)
    temp = temp.round({'freq': 2})
    print(temp.sort_values('freq', ascending=False).reset_index(drop=True).head(num_top_venues))
    print('\n')

----Allerton----
                venue  freq
0         Pizza Place  0.13
1         Supermarket  0.10
2       Deli / Bodega  0.10
3                 Spa  0.07
4  Chinese Restaurant  0.07


----Baychester----
                 venue  freq
0           Donut Shop  0.09
1   Mexican Restaurant  0.05
2                 Bank  0.05
3          Bus Station  0.05
4  Fried Chicken Joint  0.05


----Bedford Park----
                venue  freq
0               Diner  0.11
1       Deli / Bodega  0.11
2  Mexican Restaurant  0.08
3         Pizza Place  0.05
4  Chinese Restaurant  0.05


----Belmont----
                venue  freq
0  Italian Restaurant  0.18
1         Pizza Place  0.08
2       Deli / Bodega  0.08
3              Bakery  0.05
4                Bank  0.03


----Bronxdale----
                venue  freq
0  Italian Restaurant  0.08
1                Bank  0.08
2         Supermarket  0.08
3      Breakfast Spot  0.08
4  Mexican Restaurant  0.08


----Castle Hill----
         venue  freq
0         Ba

In [49]:
def return_most_common_venues(row, num_top_venues):
    row_categories = row.iloc[1:]
    row_categories_sorted = row_categories.sort_values(ascending=False)
    
    return row_categories_sorted.index.values[0:num_top_venues]

In [50]:
#Manhattan
num_top_venues = 10

indicators = ['st', 'nd', 'rd']

# create columns according to number of top venues
columns = ['Neighborhood']
for ind in np.arange(num_top_venues):
    try:
        columns.append('{}{} Most Common Venue'.format(ind+1, indicators[ind]))
    except:
        columns.append('{}th Most Common Venue'.format(ind+1))

# create a new dataframe
mneighborhoods_venues_sorted = pd.DataFrame(columns=columns)
mneighborhoods_venues_sorted['Neighborhood'] = m_grouped['Neighborhood']

for ind in np.arange(m_grouped.shape[0]):
    mneighborhoods_venues_sorted.iloc[ind, 1:] = return_most_common_venues(m_grouped.iloc[ind, :], num_top_venues)

mneighborhoods_venues_sorted.head()

Neighborhood 1st Most Common Venue 2nd Most Common Venue  \
0  Battery Park City                  Park                 Hotel   
1      Carnegie Hill           Coffee Shop                  Café   
2     Central Harlem    Seafood Restaurant    African Restaurant   
3            Chelsea           Coffee Shop                Bakery   
4          Chinatown    Chinese Restaurant                Bakery   

  3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
0           Coffee Shop         Boat or Ferry                   Gym   
1           Pizza Place             Wine Shop                   Bar   
2   American Restaurant     French Restaurant  Gym / Fitness Center   
3           Art Gallery   American Restaurant                 Hotel   
4          Cocktail Bar   American Restaurant    Salon / Barbershop   

  6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
0        Clothing Store         Memorial Site         Shopping Mall   
1           Yoga Studio                   Gym        Cosmetics Shop   
2    Chinese Restaurant                   Bar             Bookstore   
3    Italian Restaurant     French Restaurant             Wine Shop   
4                   Spa          Optical Shop          Dessert Shop   

  9th Most Common Venue 10th Most Common Venue  
0        Sandwich Place            Beer Garden  
1     French Restaurant              Bookstore  
2                  Park               Beer Bar  
3                  Café              Nightclub  
4      Greek Restaurant         Sandwich Place

In [51]:
#Brooklyn
num_top_venues = 10

indicators = ['st', 'nd', 'rd']

# create columns according to number of top venues
columns = ['Neighborhood']
for ind in np.arange(num_top_venues):
    try:
        columns.append('{}{} Most Common Venue'.format(ind+1, indicators[ind]))
    except:
        columns.append('{}th Most Common Venue'.format(ind+1))

# create a new dataframe
brneighborhoods_venues_sorted = pd.DataFrame(columns=columns)
brneighborhoods_venues_sorted['Neighborhood'] = br_grouped['Neighborhood']

for ind in np.arange(br_grouped.shape[0]):
    brneighborhoods_venues_sorted.iloc[ind, 1:] = return_most_common_venues(br_grouped.iloc[ind, :], num_top_venues)

brneighborhoods_venues_sorted.head()

Neighborhood 1st Most Common Venue 2nd Most Common Venue  \
0          Bath Beach           Pizza Place    Chinese Restaurant   
1           Bay Ridge           Pizza Place                   Spa   
2  Bedford Stuyvesant           Coffee Shop         Deli / Bodega   
3         Bensonhurst    Chinese Restaurant    Italian Restaurant   
4        Bergen Beach       Harbor / Marina        Baseball Field   

  3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
0  Cantonese Restaurant    Italian Restaurant              Pharmacy   
1    Italian Restaurant            Bagel Shop                   Bar   
2                  Café           Pizza Place                   Bar   
3            Donut Shop                  Park      Sushi Restaurant   
4                  Park            Playground    Athletics & Sports   

  6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
0           Gas Station            Donut Shop       Bubble Tea Shop   
1   American Restaurant         Grocery Store      Greek Restaurant   
2   Fried Chicken Joint              Tiki Bar                  Park   
3        Ice Cream Shop             Pet Store        Cosmetics Shop   
4                 Field               Factory    Falafel Restaurant   

  9th Most Common Venue   10th Most Common Venue  
0  Fast Food Restaurant                Surf Spot  
1      Sushi Restaurant                     Café  
2          Cocktail Bar  New American Restaurant  
3           Coffee Shop            Grocery Store  
4                  Farm           Farmers Market

In [52]:
#Queens
num_top_venues = 10

indicators = ['st', 'nd', 'rd']

# create columns according to number of top venues
columns = ['Neighborhood']
for ind in np.arange(num_top_venues):
    try:
        columns.append('{}{} Most Common Venue'.format(ind+1, indicators[ind]))
    except:
        columns.append('{}th Most Common Venue'.format(ind+1))

# create a new dataframe
qneighborhoods_venues_sorted = pd.DataFrame(columns=columns)
qneighborhoods_venues_sorted['Neighborhood'] = q_grouped['Neighborhood']

for ind in np.arange(q_grouped.shape[0]):
    qneighborhoods_venues_sorted.iloc[ind, 1:] = return_most_common_venues(q_grouped.iloc[ind, :], num_top_venues)

mneighborhoods_venues_sorted.head()

Neighborhood 1st Most Common Venue 2nd Most Common Venue  \
0  Battery Park City                  Park                 Hotel   
1      Carnegie Hill           Coffee Shop                  Café   
2     Central Harlem    Seafood Restaurant    African Restaurant   
3            Chelsea           Coffee Shop                Bakery   
4          Chinatown    Chinese Restaurant                Bakery   

  3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
0           Coffee Shop         Boat or Ferry                   Gym   
1           Pizza Place             Wine Shop                   Bar   
2   American Restaurant     French Restaurant  Gym / Fitness Center   
3           Art Gallery   American Restaurant                 Hotel   
4          Cocktail Bar   American Restaurant    Salon / Barbershop   

  6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
0        Clothing Store         Memorial Site         Shopping Mall   
1           Yoga Studio                   Gym        Cosmetics Shop   
2    Chinese Restaurant                   Bar             Bookstore   
3    Italian Restaurant     French Restaurant             Wine Shop   
4                   Spa          Optical Shop          Dessert Shop   

  9th Most Common Venue 10th Most Common Venue  
0        Sandwich Place            Beer Garden  
1     French Restaurant              Bookstore  
2                  Park               Beer Bar  
3                  Café              Nightclub  
4      Greek Restaurant         Sandwich Place

In [53]:
#Staten Island
num_top_venues = 10

indicators = ['st', 'nd', 'rd']

# create columns according to number of top venues
columns = ['Neighborhood']
for ind in np.arange(num_top_venues):
    try:
        columns.append('{}{} Most Common Venue'.format(ind+1, indicators[ind]))
    except:
        columns.append('{}th Most Common Venue'.format(ind+1))

# create a new dataframe
sneighborhoods_venues_sorted = pd.DataFrame(columns=columns)
sneighborhoods_venues_sorted['Neighborhood'] = s_grouped['Neighborhood']

for ind in np.arange(s_grouped.shape[0]):
    sneighborhoods_venues_sorted.iloc[ind, 1:] = return_most_common_venues(s_grouped.iloc[ind, :], num_top_venues)

sneighborhoods_venues_sorted.head()

Neighborhood 1st Most Common Venue 2nd Most Common Venue  \
0       Annadale           Pizza Place            Restaurant   
1  Arden Heights         Deli / Bodega           Pizza Place   
2      Arlington         Deli / Bodega         Boat or Ferry   
3       Arrochar    Italian Restaurant           Pizza Place   
4    Bay Terrace           Supermarket    Italian Restaurant   

  3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
0        Cosmetics Shop                   Pub         Train Station   
1           Coffee Shop              Pharmacy            Food Truck   
2              Bus Stop           Coffee Shop         Grocery Store   
3            Bagel Shop         Deli / Bodega              Bus Stop   
4      Sushi Restaurant            Donut Shop    Salon / Barbershop   

  6th Most Common Venue 7th Most Common Venue     8th Most Common Venue  \
0                 Diner                  Food              Liquor Store   
1     Food & Drink Shop                  Food               Flower Shop   
2   Filipino Restaurant     French Restaurant                Food Truck   
3            Taco Place          Liquor Store  Mediterranean Restaurant   
4        Shipping Store      Insurance Office        Athletics & Sports   

       9th Most Common Venue 10th Most Common Venue  
0                Yoga Studio            Event Space  
1          Fish & Chips Shop    Filipino Restaurant  
2          Food & Drink Shop                   Food  
3  Middle Eastern Restaurant             Food Truck  
4             Farmers Market      French Restaurant

In [54]:
#Bronx
num_top_venues = 10

indicators = ['st', 'nd', 'rd']

# create columns according to number of top venues
columns = ['Neighborhood']
for ind in np.arange(num_top_venues):
    try:
        columns.append('{}{} Most Common Venue'.format(ind+1, indicators[ind]))
    except:
        columns.append('{}th Most Common Venue'.format(ind+1))

# create a new dataframe
bxneighborhoods_venues_sorted = pd.DataFrame(columns=columns)
bxneighborhoods_venues_sorted['Neighborhood'] = bx_grouped['Neighborhood']

for ind in np.arange(bx_grouped.shape[0]):
    bxneighborhoods_venues_sorted.iloc[ind, 1:] = return_most_common_venues(bx_grouped.iloc[ind, :], num_top_venues)

bxneighborhoods_venues_sorted.head()

Neighborhood 1st Most Common Venue 2nd Most Common Venue  \
0      Allerton           Pizza Place         Deli / Bodega   
1    Baychester            Donut Shop    Spanish Restaurant   
2  Bedford Park         Deli / Bodega                 Diner   
3       Belmont    Italian Restaurant           Pizza Place   
4     Bronxdale        Breakfast Spot                  Bank   

   3rd Most Common Venue          4th Most Common Venue 5th Most Common Venue  \
0            Supermarket             Chinese Restaurant                   Spa   
1   Fast Food Restaurant                  Boat or Ferry        Mattress Store   
2     Mexican Restaurant                    Bus Station        Sandwich Place   
3          Deli / Bodega                         Bakery            Donut Shop   
4  Performing Arts Venue  Paper / Office Supplies Store    Chinese Restaurant   

         6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
0         Fast Food Restaurant        Breakfast Spot      Department Store   
1            Food & Drink Shop           Men's Store           Bus Station   
2                  Pizza Place    Chinese Restaurant            Smoke Shop   
3                 Dessert Shop    Spanish Restaurant                  Bank   
4  Eastern European Restaurant    Mexican Restaurant    Spanish Restaurant   

  9th Most Common Venue 10th Most Common Venue  
0           Bus Station  Check Cashing Service  
1    Mexican Restaurant         Sandwich Place  
2            Donut Shop                   Park  
3         Grocery Store      Food & Drink Shop  
4           Pizza Place            Supermarket

In [58]:
kclusters = 5

m_grouped_clustering = m_grouped.drop('Neighborhood', 1)

# run k-means clustering
mkmeans = KMeans(n_clusters=kclusters, random_state=0).fit(m_grouped_clustering)

# check cluster labels generated for each row in the dataframe
mkmeans.labels_[0:10] 

array([1, 1, 0, 1, 1, 0, 1, 4, 1, 1], dtype=int32)

In [59]:
kclusters = 5

br_grouped_clustering = br_grouped.drop('Neighborhood', 1)

# run k-means clustering
brkmeans = KMeans(n_clusters=kclusters, random_state=0).fit(br_grouped_clustering)

# check cluster labels generated for each row in the dataframe
brkmeans.labels_[0:10] 

array([0, 4, 4, 4, 1, 4, 0, 4, 4, 4], dtype=int32)

In [60]:
kclusters = 5

q_grouped_clustering = q_grouped.drop('Neighborhood', 1)

# run k-means clustering
qkmeans = KMeans(n_clusters=kclusters, random_state=0).fit(q_grouped_clustering)

# check cluster labels generated for each row in the dataframe
qkmeans.labels_[0:10] 

array([2, 2, 2, 2, 2, 2, 4, 2, 2, 2], dtype=int32)

In [61]:
kclusters = 5

s_grouped_clustering = s_grouped.drop('Neighborhood', 1)

# run k-means clustering
skmeans = KMeans(n_clusters=kclusters, random_state=0).fit(s_grouped_clustering)

# check cluster labels generated for each row in the dataframe
skmeans.labels_[0:10] 

array([1, 1, 2, 1, 1, 2, 1, 1, 1, 1], dtype=int32)

In [62]:
kclusters = 5

bx_grouped_clustering = bx_grouped.drop('Neighborhood', 1)

# run k-means clustering
bxkmeans = KMeans(n_clusters=kclusters, random_state=0).fit(bx_grouped_clustering)

# check cluster labels generated for each row in the dataframe
bxkmeans.labels_[0:10] 

array([2, 2, 2, 0, 0, 0, 0, 2, 4, 2], dtype=int32)

In [71]:

m_merged = manhattan_data

# merge manhattan_grouped with manhattan_data to add latitude/longitude for each neighborhood
m_merged = m_merged.join(mneighborhoods_venues_sorted.set_index('Neighborhood'), on='Neighborhood')

m_merged.head() # check the last columns!

Borough        Neighborhood   Latitude  Longitude  Cluster Labels  \
0  Manhattan         Marble Hill  40.876551 -73.910660               3   
1  Manhattan           Chinatown  40.715618 -73.994279               1   
2  Manhattan  Washington Heights  40.851903 -73.936900               4   
3  Manhattan              Inwood  40.867684 -73.921210               4   
4  Manhattan    Hamilton Heights  40.823604 -73.949688               4   

  1st Most Common Venue 2nd Most Common Venue 3rd Most Common Venue  \
0                   Gym        Sandwich Place        Discount Store   
1    Chinese Restaurant                Bakery          Cocktail Bar   
2                  Café                Bakery    Chinese Restaurant   
3    Mexican Restaurant                  Café                Lounge   
4           Pizza Place    Mexican Restaurant                  Café   

  4th Most Common Venue 5th Most Common Venue      6th Most Common Venue  \
0           Coffee Shop           Yoga Studio           Video Game Store   
1   American Restaurant    Salon / Barbershop                        Spa   
2     Mobile Phone Shop         Grocery Store  Latin American Restaurant   
3            Restaurant           Pizza Place              Deli / Bodega   
4           Coffee Shop         Deli / Bodega                Yoga Studio   

  7th Most Common Venue 8th Most Common Venue      9th Most Common Venue  \
0    Seafood Restaurant        Tennis Stadium                 Donut Shop   
1          Optical Shop          Dessert Shop           Greek Restaurant   
2                  Bank    Italian Restaurant           Tapas Restaurant   
3    Spanish Restaurant              Wine Bar         Frozen Yogurt Shop   
4                  Park     Indian Restaurant  Latin American Restaurant   

  10th Most Common Venue  
0        Supplement Shop  
1         Sandwich Place  
2                    Gym  
3                 Bakery  
4           Cocktail Bar

In [80]:
brneighborhoods_venues_sorted.insert(0, 'Cluster Labels', brkmeans.labels_)

br_merged = br_data

br_merged = br_merged.join(brneighborhoods_venues_sorted.set_index('Neighborhood'), on='Neighborhood')

br_merged.head() 

Borough Neighborhood   Latitude  Longitude  Cluster Labels  \
0  Brooklyn    Bay Ridge  40.625801 -74.030621               4   
1  Brooklyn  Bensonhurst  40.611009 -73.995180               4   
2  Brooklyn  Sunset Park  40.645103 -74.010316               0   
3  Brooklyn   Greenpoint  40.730201 -73.954241               4   
4  Brooklyn    Gravesend  40.595260 -73.973471               0   

  1st Most Common Venue 2nd Most Common Venue      3rd Most Common Venue  \
0           Pizza Place                   Spa         Italian Restaurant   
1    Chinese Restaurant    Italian Restaurant                 Donut Shop   
2                  Bank                Bakery  Latin American Restaurant   
3                   Bar           Pizza Place                Coffee Shop   
4                Lounge           Pizza Place         Chinese Restaurant   

  4th Most Common Venue 5th Most Common Venue 6th Most Common Venue  \
0            Bagel Shop                   Bar   American Restaurant   
1                  Park      Sushi Restaurant        Ice Cream Shop   
2    Mexican Restaurant           Pizza Place                   Gym   
3          Cocktail Bar           Yoga Studio         Grocery Store   
4    Italian Restaurant                Bakery              Pharmacy   

  7th Most Common Venue 8th Most Common Venue 9th Most Common Venue  \
0         Grocery Store      Greek Restaurant      Sushi Restaurant   
1             Pet Store        Cosmetics Shop           Coffee Shop   
2   Fried Chicken Joint              Pharmacy     Mobile Phone Shop   
3           Record Shop     French Restaurant    Mexican Restaurant   
4   Martial Arts School                   Bar         Metro Station   

  10th Most Common Venue  
0                   Café  
1          Grocery Store  
2         Sandwich Place  
3                   Café  
4             Donut Shop

In [81]:
qneighborhoods_venues_sorted.insert(0, 'Cluster Labels', qkmeans.labels_)

q_merged = q_data

q_merged = q_merged.join(qneighborhoods_venues_sorted.set_index('Neighborhood'), on='Neighborhood')

q_merged.head() 

Borough     Neighborhood   Latitude  Longitude  Cluster Labels  \
0  Queens          Astoria  40.768509 -73.915654               2   
1  Queens         Woodside  40.746349 -73.901842               2   
2  Queens  Jackson Heights  40.751981 -73.882821               2   
3  Queens         Elmhurst  40.744049 -73.881656               2   
4  Queens     Howard Beach  40.654225 -73.838138               2   

       1st Most Common Venue      2nd Most Common Venue  \
0                        Bar  Middle Eastern Restaurant   
1              Grocery Store                     Bakery   
2  Latin American Restaurant        Peruvian Restaurant   
3            Thai Restaurant         Mexican Restaurant   
4         Italian Restaurant                   Pharmacy   

       3rd Most Common Venue 4th Most Common Venue     5th Most Common Venue  \
0         Seafood Restaurant                Bakery  Mediterranean Restaurant   
1  Latin American Restaurant       Thai Restaurant       Filipino Restaurant   
2  South American Restaurant                Bakery         Mobile Phone Shop   
3         Chinese Restaurant       Bubble Tea Shop     Vietnamese Restaurant   
4       Fast Food Restaurant        Clothing Store            Sandwich Place   

       6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
0                       Café      Greek Restaurant            Hookah Bar   
1                 Donut Shop   American Restaurant    Chinese Restaurant   
2              Grocery Store       Thai Restaurant            Shoe Store   
3  South American Restaurant           Snack Place    Seafood Restaurant   
4              Deli / Bodega    Chinese Restaurant      Tapas Restaurant   

  9th Most Common Venue 10th Most Common Venue  
0     Indian Restaurant             Bagel Shop  
1                   Pub                    Bar  
2       Supplement Shop    Empanada Restaurant  
3      Malay Restaurant             Food Court  
4        Shipping Store          Jewelry Store

In [82]:
sneighborhoods_venues_sorted.insert(0, 'Cluster Labels', skmeans.labels_)

s_merged = s_data

s_merged = s_merged.join(sneighborhoods_venues_sorted.set_index('Neighborhood'), on='Neighborhood')

s_merged.head() 

Borough   Neighborhood   Latitude  Longitude  Cluster Labels  \
0  Staten Island     St. George  40.644982 -74.079353             1.0   
1  Staten Island   New Brighton  40.640615 -74.087017             2.0   
2  Staten Island      Stapleton  40.626928 -74.077902             1.0   
3  Staten Island       Rosebank  40.615305 -74.069805             1.0   
4  Staten Island  West Brighton  40.631879 -74.107182             1.0   

  1st Most Common Venue 2nd Most Common Venue 3rd Most Common Venue  \
0        Clothing Store    Italian Restaurant   Sporting Goods Shop   
1              Bus Stop         Deli / Bodega                  Park   
2           Pizza Place                  Bank        Discount Store   
3    Italian Restaurant         Grocery Store    Mexican Restaurant   
4           Coffee Shop    Italian Restaurant        Breakfast Spot   

  4th Most Common Venue 5th Most Common Venue 6th Most Common Venue  \
0                   Bar      Baseball Stadium   Monument / Landmark   
1            Playground         Bowling Alley        Discount Store   
2              Bus Stop            Restaurant        Sandwich Place   
3                Museum            Nail Salon   Filipino Restaurant   
4           Music Store              Pharmacy                  Bank   

  7th Most Common Venue 8th Most Common Venue 9th Most Common Venue  \
0           Snack Place        Scenic Lookout        Sandwich Place   
1            Donut Shop           Dry Cleaner     French Restaurant   
2                   Bar    Seafood Restaurant    Mexican Restaurant   
3        Discount Store        Breakfast Spot      Storage Facility   
4                   Bar            Board Shop     Food & Drink Shop   

  10th Most Common Venue  
0                  Plaza  
1             Food Truck  
2     Spanish Restaurant  
3         Sandwich Place  
4             Bagel Shop

In [83]:
bxneighborhoods_venues_sorted.insert(0, 'Cluster Labels', bxkmeans.labels_)

bx_merged = bx_data

bx_merged = bx_merged.join(bxneighborhoods_venues_sorted.set_index('Neighborhood'), on='Neighborhood')

bx_merged.head() 

Borough Neighborhood   Latitude  Longitude  Cluster Labels  \
0   Bronx    Wakefield  40.894705 -73.847201               0   
1   Bronx   Co-op City  40.874294 -73.829939               2   
2   Bronx  Eastchester  40.887556 -73.827806               2   
3   Bronx    Fieldston  40.895437 -73.905643               1   
4   Bronx    Riverdale  40.890834 -73.912585               1   

  1st Most Common Venue 2nd Most Common Venue 3rd Most Common Venue  \
0              Pharmacy        Ice Cream Shop            Laundromat   
1  Fast Food Restaurant     Accessories Store        Baseball Field   
2  Caribbean Restaurant           Bus Station                 Diner   
3                 Plaza  Medical Supply Store                 River   
4           Bus Station                  Park                 Plaza   

  4th Most Common Venue 5th Most Common Venue 6th Most Common Venue  \
0          Dessert Shop        Sandwich Place            Donut Shop   
1         Grocery Store   Fried Chicken Joint                  Park   
2         Deli / Bodega         Bowling Alley     Convenience Store   
3           Bus Station     Electronics Store                  Food   
4  Medical Supply Store        Baseball Field                   Gym   

  7th Most Common Venue 8th Most Common Venue 9th Most Common Venue  \
0           Gas Station         Deli / Bodega  Gym / Fitness Center   
1        Discount Store              Pharmacy           Pizza Place   
2            Donut Shop    Chinese Restaurant    Seafood Restaurant   
3           Fish Market     Fish & Chips Shop           Film Studio   
4                  Bank        Farmers Market                  Food   

  10th Most Common Venue  
0               Dive Bar  
1          Deli / Bodega  
2   Fast Food Restaurant  
3   Fast Food Restaurant  
4            Fish Market

In [77]:
# create Manhattan map
mmap_clusters = folium.Map(location=[latitude, longitude], zoom_start=11)

# set color scheme for the clusters
x = np.arange(kclusters)
ys = [i + x + (i*x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# add markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(m_merged['Latitude'], m_merged['Longitude'], m_merged['Neighborhood'], m_merged['Cluster Labels']):
    label = folium.Popup(str(poi) + ' Cluster ' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[cluster-1],
        fill=True,
        fill_color=rainbow[cluster-1],
        fill_opacity=0.7).add_to(mmap_clusters)
       
mmap_clusters

In [84]:
# create Manhattan map
brmap_clusters = folium.Map(location=[latitude, longitude], zoom_start=11)

# set color scheme for the clusters
x = np.arange(kclusters)
ys = [i + x + (i*x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# add markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(br_merged['Latitude'], br_merged['Longitude'], br_merged['Neighborhood'], br_merged['Cluster Labels']):
    label = folium.Popup(str(poi) + ' Cluster ' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[cluster-1],
        fill=True,
        fill_color=rainbow[cluster-1],
        fill_opacity=0.7).add_to(brmap_clusters)
       
brmap_clusters

In [90]:
# create Manhattan map
qmap_clusters = folium.Map(location=[latitude, longitude], zoom_start=11)

# set color scheme for the clusters
x = np.arange(kclusters)
ys = [i + x + (i*x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# add markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(q_merged['Latitude'], q_merged['Longitude'], q_merged['Neighborhood'], q_merged['Cluster Labels']):
    label = folium.Popup(str(poi) + ' Cluster ' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[cluster-1],
        fill=True,
        fill_color=rainbow[cluster-1],
        fill_opacity=0.7).add_to(brmap_clusters)
       
qmap_clusters

In [92]:
# create Manhattan map
smap_clusters = folium.Map(location=[latitude, longitude], zoom_start=11)

# set color scheme for the clusters
x = np.arange(kclusters)
ys = [i + x + (i*x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# add markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(s_merged['Latitude'], s_merged['Longitude'], s_merged['Neighborhood'], s_merged['Cluster Labels']):
    label = folium.Popup(str(poi) + ' Cluster ' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[int(cluster)-1],
        fill=True,
        fill_color=rainbow[int(cluster)-1],
        fill_opacity=0.7).add_to(brmap_clusters)
       
smap_clusters

ValueError: cannot convert float NaN to integer

In [95]:
#Man
#Cluster1
m_merged.loc[m_merged['Cluster Labels'] == 0, m_merged.columns[[1] + list(range(5, m_merged.shape[1]))]]


Neighborhood 1st Most Common Venue 2nd Most Common Venue  \
6      Central Harlem    Seafood Restaurant    African Restaurant   
11   Roosevelt Island                  Park            Playground   
18  Greenwich Village    Italian Restaurant      Sushi Restaurant   
21            Tribeca    Italian Restaurant                  Park   
24       West Village    Italian Restaurant             Jazz Club   
32       Civic Center           Coffee Shop                   Spa   
35         Turtle Bay           Coffee Shop    Italian Restaurant   
39       Hudson Yards   American Restaurant  Gym / Fitness Center   

      3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
6       American Restaurant     French Restaurant  Gym / Fitness Center   
11              Coffee Shop  Gym / Fitness Center          Liquor Store   
18                     Café        Clothing Store   American Restaurant   
21      American Restaurant                   Spa              Wine Bar   
24  New American Restaurant          Cocktail Bar                  Park   
32     Gym / Fitness Center                 Hotel     French Restaurant   
35         Sushi Restaurant   Japanese Restaurant         Deli / Bodega   
39                    Hotel    Italian Restaurant          Burger Joint   

   6th Most Common Venue 7th Most Common Venue  8th Most Common Venue  \
6     Chinese Restaurant                   Bar              Bookstore   
11      Greek Restaurant        Sandwich Place  Outdoors & Recreation   
18     Indian Restaurant       Bubble Tea Shop      French Restaurant   
21           Men's Store           Coffee Shop                   Café   
24           Coffee Shop        Cosmetics Shop                Theater   
32          Cocktail Bar           Yoga Studio                   Park   
35                  Park                  Café     Seafood Restaurant   
39                  Park             Nightclub                   Café   

   9th Most Common Venue 10th Most Common Venue  
6                   Park               Beer Bar  
11        Scenic Lookout                 School  
18          Dessert Shop      Accessories Store  
21        Scenic Lookout       Greek Restaurant  
24   American Restaurant               Wine Bar  
32    Italian Restaurant    American Restaurant  
35      Ramen Restaurant     Turkish Restaurant  
39               Dog Run                    Gym

In [96]:
#Man
#Cluster 2 
m_merged.loc[m_merged['Cluster Labels'] == 1, m_merged.columns[[1] + list(range(5, m_merged.shape[1]))]]

Neighborhood    1st Most Common Venue 2nd Most Common Venue  \
1             Chinatown       Chinese Restaurant                Bakery   
8       Upper East Side       Italian Restaurant           Coffee Shop   
9             Yorkville       Italian Restaurant                   Gym   
10           Lenox Hill         Sushi Restaurant    Italian Restaurant   
12      Upper West Side       Italian Restaurant                   Bar   
13       Lincoln Square     Gym / Fitness Center                  Café   
14              Clinton                  Theater  Gym / Fitness Center   
15              Midtown                    Hotel           Coffee Shop   
16          Murray Hill              Coffee Shop                 Hotel   
17              Chelsea              Coffee Shop                Bakery   
19         East Village                      Bar    Mexican Restaurant   
22         Little Italy                   Bakery                  Café   
23                 Soho           Clothing Store    Italian Restaurant   
25     Manhattan Valley                      Bar           Coffee Shop   
26  Morningside Heights              Coffee Shop                  Park   
27             Gramercy                      Bar            Bagel Shop   
28    Battery Park City                     Park                 Hotel   
29   Financial District              Coffee Shop           Pizza Place   
30        Carnegie Hill              Coffee Shop                  Café   
31                 Noho       Italian Restaurant           Pizza Place   
33        Midtown South        Korean Restaurant   Japanese Restaurant   
34         Sutton Place       Italian Restaurant  Gym / Fitness Center   
38             Flatiron  New American Restaurant   American Restaurant   

     3rd Most Common Venue     4th Most Common Venue 5th Most Common Venue  \
1             Cocktail Bar       American Restaurant    Salon / Barbershop   
8                   Bakery                   Exhibit  Gym / Fitness Center   
9                      Bar               Coffee Shop         Deli / Bodega   
10             Coffee Shop               Pizza Place          Cocktail Bar   
12                  Bakery                  Wine Bar          Dessert Shop   
13                   Plaza     Performing Arts Venue               Theater   
14             Coffee Shop       American Restaurant    Italian Restaurant   
15     Sporting Goods Shop                Steakhouse               Theater   
16                     Bar            Sandwich Place   American Restaurant   
17             Art Gallery       American Restaurant                 Hotel   
19            Cocktail Bar            Ice Cream Shop           Pizza Place   
22      Italian Restaurant           Bubble Tea Shop                 Hotel   
23             Coffee Shop  Mediterranean Restaurant    Salon / Barbershop   
25       Indian Restaurant           Thai Restaurant            Playground   
26               Bookstore       American Restaurant         Deli / Bodega   
27             Coffee Shop        Italian Restaurant           Pizza Place   
28             Coffee Shop             Boat or Ferry                   Gym   
29      Italian Restaurant              Cocktail Bar           Salad Place   
30             Pizza Place                 Wine Shop                   Bar   
31                   Hotel              Cocktail Bar           Coffee Shop   
33                   Hotel       American Restaurant           Salad Place   
34  Furniture / Home Store                       Gym           Pizza Place   
38      Italian Restaurant       Japanese Restaurant           Coffee Shop   

    6th Most Common Venue   7th Most Common Venue  \
1                     Spa            Optical Shop   
8             Yoga Studio             Pizza Place   
9        Sushi Restaurant                   Diner   
10          Deli / Bodega            Burger Joint   
12      Indian Restaurant                    Café   
13           Concert Hall               Win

In [97]:
#Man
#Cluster 3
m_merged.loc[m_merged['Cluster Labels'] == 2, m_merged.columns[[1] + list(range(5, m_merged.shape[1]))]]

Neighborhood 1st Most Common Venue 2nd Most Common Venue  \
37  Stuyvesant Town                   Bar                  Park   

   3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
37           Coffee Shop         Boat or Ferry           Pet Service   

   6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
37  Gym / Fitness Center        Baseball Field              Fountain   

   9th Most Common Venue 10th Most Common Venue  
37       Harbor / Marina           Skating Rink

In [98]:
#Man
#Cluster 4
m_merged.loc[m_merged['Cluster Labels'] == 3, m_merged.columns[[1] + list(range(5, m_merged.shape[1]))]]

Neighborhood 1st Most Common Venue 2nd Most Common Venue  \
0  Marble Hill                   Gym        Sandwich Place   

  3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
0        Discount Store           Coffee Shop           Yoga Studio   

  6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
0      Video Game Store    Seafood Restaurant        Tennis Stadium   

  9th Most Common Venue 10th Most Common Venue  
0            Donut Shop        Supplement Shop

In [99]:
#Man
#Cluster 5
m_merged.loc[m_merged['Cluster Labels'] == 4, m_merged.columns[[1] + list(range(5, m_merged.shape[1]))]]

Neighborhood 1st Most Common Venue 2nd Most Common Venue  \
2   Washington Heights                  Café                Bakery   
3               Inwood    Mexican Restaurant                  Café   
4     Hamilton Heights           Pizza Place    Mexican Restaurant   
5       Manhattanville           Coffee Shop    Seafood Restaurant   
7          East Harlem    Mexican Restaurant       Thai Restaurant   
20     Lower East Side           Art Gallery    Chinese Restaurant   
36          Tudor City                  Café                  Park   

   3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
2     Chinese Restaurant     Mobile Phone Shop         Grocery Store   
3                 Lounge            Restaurant           Pizza Place   
4                   Café           Coffee Shop         Deli / Bodega   
5     Italian Restaurant    Mexican Restaurant         Deli / Bodega   
7                 Bakery        Sandwich Place                  Park   
20           Coffee Shop                Bakery                  Café   
36    Mexican Restaurant           Pizza Place         Deli / Bodega   

        6th Most Common Venue      7th Most Common Venue  \
2   Latin American Restaurant                       Bank   
3               Deli / Bodega         Spanish Restaurant   
4                 Yoga Studio                       Park   
5                        Café                     Bakery   
7               Deli / Bodega  Latin American Restaurant   
20           Ramen Restaurant        Japanese Restaurant   
36                Coffee Shop                      Diner   

      8th Most Common Venue      9th Most Common Venue 10th Most Common Venue  
2        Italian Restaurant           Tapas Restaurant                    Gym  
3                  Wine Bar         Frozen Yogurt Shop                 Bakery  
4         Indian Restaurant  Latin American Restaurant           Cocktail Bar  
5                      Bank                        Bar     Spanish Restaurant  
7   New American Restaurant                        Gym          Grocery Store  
20            Grocery Store                   Pharmacy                   Park  
36         Sushi Restaurant                    Dog Run       Greek Restaurant

In [103]:
#Brooklyn
print("Brooklyn: Cluster 1")
br_merged.loc[br_merged['Cluster Labels'] == 0, br_merged.columns[[1] + list(range(5, br_merged.shape[1]))]]


Brooklyn: Cluster 1


Neighborhood 1st Most Common Venue 2nd Most Common Venue  \
2         Sunset Park                  Bank                Bakery   
4           Gravesend                Lounge           Pizza Place   
7   Manhattan Terrace           Pizza Place        Ice Cream Shop   
9       Crown Heights           Pizza Place                Museum   
33         Bath Beach           Pizza Place    Chinese Restaurant   
34       Borough Park                  Bank           Pizza Place   
46            Midwood           Pizza Place        Ice Cream Shop   
48         Georgetown                  Bank              Pharmacy   
52      Ocean Parkway           Pizza Place            Playground   
53      Fort Hamilton           Pizza Place              Bus Stop   
60         Mill Basin    Chinese Restaurant           Pizza Place   
66          Homecrest                  Bank            Donut Shop   
68            Madison            Bagel Shop         Deli / Bodega   

            3rd Most Common Venue 4th Most Common Venue  \
2       Latin American Restaurant    Mexican Restaurant   
4              Chinese Restaurant    Italian Restaurant   
7                      Donut Shop            Bagel Shop   
9                            Café           Coffee Shop   
33           Cantonese Restaurant    Italian Restaurant   
34                       Pharmacy  Fast Food Restaurant   
46               Video Game Store     Convenience Store   
48                 Breakfast Spot            Donut Shop   
52  Paper / Office Supplies Store          Liquor Store   
53           Gym / Fitness Center        Sandwich Place   
60                           Bank            Bagel Shop   
66             Chinese Restaurant      Sushi Restaurant   
68                    Pizza Place           Candy Store   

    5th Most Common Venue      6th Most Common Venue 7th Most Common Venue  \
2             Pizza Place                        Gym   Fried Chicken Joint   
4                  Bakery                   Pharmacy   Martial Arts School   
7       Convenience Store                 Steakhouse         Grocery Store   
9              Playground                  Bookstore           Supermarket   
33               Pharmacy                Gas Station            Donut Shop   
34             Restaurant                       Café         Deli / Bodega   
46               Pharmacy                Candy Store         Moving Target   
48     Italian Restaurant              Shopping Mall           Supermarket   
52  General Entertainment           Sushi Restaurant           Supermarket   
53     Italian Restaurant         Chinese Restaurant              Pharmacy   
60    Japanese Restaurant  Middle Eastern Restaurant          Burger Joint   
66     Mexican Restaurant              Grocery Store           Pizza Place   
68     Chinese Restaurant                 Restaurant            Hobby Shop   

   8th Most Common Venue 9th Most Common Venue 10th Most Common Venue  
2               Pharmacy     Mobile Phone Shop         Sandwich Place  
4                    Bar         Metro Station             Donut Shop  
7                    Gym           Coffee Shop                   Bank  
9            Candy Store    Salon / Barbershop           Burger Joint  
33       Bubble Tea Shop  Fast Food Restaurant              Surf Spot  
34                 Hotel    Chinese Restaurant    American Restaurant  
46                Bakery         Deli / Bodega         History Museum  
48    Frozen Yogurt Shop    Miscellaneous Shop           Burger Joint  
52            Steakhouse            Restaurant                    Gym  
53                 Diner                  Café           Cocktail Bar  
60           Supermarket        Breakfast Spot     Frozen Yogurt Shop  
66        Sandwich Place    Russian Restaurant   Fast Food Restaurant  
68                   Spa    Italian Restaurant           Dessert Shop

In [104]:
print("Brooklyn: Cluster 2")
br_merged.loc[br_merged['Cluster Labels'] == 1, br_merged.columns[[1] + list(range(5, br_merged.shape[1]))]]


Brooklyn: Cluster 2


Neighborhood 1st Most Common Venue 2nd Most Common Venue  \
31  Manhattan Beach                  Café              Bus Stop   
45     Bergen Beach       Harbor / Marina        Baseball Field   

   3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
31            Playground       Harbor / Marina                 Beach   
45                  Park            Playground    Athletics & Sports   

   6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
31        Sandwich Place        Ice Cream Shop                  Food   
45                 Field               Factory    Falafel Restaurant   

   9th Most Common Venue 10th Most Common Venue  
31           Flower Shop            Flea Market  
45                  Farm         Farmers Market

In [105]:

print("Brooklyn: Cluster 3")
br_merged.loc[br_merged['Cluster Labels'] == 2, br_merged.columns[[1] + list(range(5, br_merged.shape[1]))]]



Brooklyn: Cluster 3


Neighborhood 1st Most Common Venue 2nd Most Common Venue  \
30  Mill Island                  Pool         Women's Store   

   3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
30     Fish & Chips Shop               Factory    Falafel Restaurant   

   6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
30                  Farm        Farmers Market  Fast Food Restaurant   

   9th Most Common Venue 10th Most Common Venue  
30                 Field            Fish Market

In [106]:
print("Brooklyn: Cluster 4")
br_merged.loc[br_merged['Cluster Labels'] == 3, br_merged.columns[[1] + list(range(5, br_merged.shape[1]))]]


Brooklyn: Cluster 4


Neighborhood      1st Most Common Venue 2nd Most Common Venue  \
8              Flatbush                   Pharmacy           Coffee Shop   
10        East Flatbush         Chinese Restaurant            Print Shop   
14          Brownsville              Moving Target   Fried Chicken Joint   
25        Cypress Hills  Latin American Restaurant   Fried Chicken Joint   
26        East New York              Deli / Bodega    Chinese Restaurant   
27        Starrett City                Supermarket         Moving Target   
28             Canarsie                        Gym  Caribbean Restaurant   
29            Flatlands                   Pharmacy  Caribbean Restaurant   
37          Marine Park              Deli / Bodega       Doctor's Office   
39             Sea Gate                Bus Station   American Restaurant   
47  Prospect Park South       Caribbean Restaurant           Pizza Place   
56                Rugby             Sandwich Place         Grocery Store   
57       Remsen Village       Caribbean Restaurant  Fast Food Restaurant   
58             New Lots        Fried Chicken Joint           Pizza Place   
63           Weeksville              Deli / Bodega    Chinese Restaurant   
69              Erasmus       Caribbean Restaurant           Yoga Studio   

   3rd Most Common Venue   4th Most Common Venue      5th Most Common Venue  \
8   Caribbean Restaurant      Mexican Restaurant                  Juice Bar   
10          Liquor Store                Pharmacy                       Park   
14                 Trail                   Plaza                 Playground   
25        Ice Cream Shop      Spanish Restaurant              Metro Station   
26  Fast Food Restaurant             Pizza Place  Latin American Restaurant   
27        Cosmetics Shop             Bus Station                   Bus Stop   
28    Chinese Restaurant        Asian Restaurant                    Factory   
29   Fried Chicken Joint    Fast Food Restaurant                       Park   
37          Soccer Field      Chinese Restaurant           Basketball Court   
39          Home Service                   Beach                        Spa   
47         Grocery Store       Mobile Phone Shop       Fast Food Restaurant   
56                  Bank    Caribbean Restaurant       Fast Food Restaurant   
57        Breakfast Spot              Donut Shop        Fried Chicken Joint   
58        Discount Store                Pharmacy         Chinese Restaurant   
63        Discount Store        Department Store               Liquor Store   
69              Pharmacy  Furniture / Home Store                Music Venue   

   6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
8          Deli / Bodega            Bagel Shop           Pizza Place   
10  Caribbean Restaurant  Fast Food Restaurant         Moving Target   
14           Pizza Place     Convenience Store    Spanish Restaurant   
25  Fast Food Restaurant    Chinese Restaurant         Deli / Bodega   
26         Metro Station              Pharmacy                 Plaza   
27  Caribbean Restaurant                 River            Donut Shop   
28    Falafel Restaurant                  Farm        Farmers Market   
29                Lounge        Discount Store                   Bar   
37        Baseball Field    Athletics & Sports              Pharmacy   
39            Food Court            Food Stand     Food & Drink Shop   
47      Department Store   Fried Chicken Joint    Mexican Restaurant   
56     Mobile Phone Shop    Salon / Barbershop           Gas Station   
57           Supermarket           Fish Market           Gas Station   
58        Breakfast Spot                  Bank         Metro Station   
63           Gas Station            Donut Shop         Grocery Store   
69           Supermarket         Grocery Store                  Bank   

        9th Most Common Venue     10th Most Common Venue  
8                  Donut Shop         Chinese Restaurant  
10                Supermarket  

In [107]:
print("Brooklyn: Cluster 5")
br_merged.loc[br_merged['Cluster Labels'] == 4, br_merged.columns[[1] + list(range(5, br_merged.shape[1]))]]

Brooklyn: Cluster 5


Neighborhood        1st Most Common Venue  \
0                   Bay Ridge                  Pizza Place   
1                 Bensonhurst           Chinese Restaurant   
3                  Greenpoint                          Bar   
5              Brighton Beach  Eastern European Restaurant   
6              Sheepshead Bay                 Dessert Shop   
11                 Kensington                Grocery Store   
12            Windsor Terrace                        Diner   
13           Prospect Heights                          Bar   
15               Williamsburg                  Pizza Place   
16                   Bushwick                          Bar   
17         Bedford Stuyvesant                  Coffee Shop   
18           Brooklyn Heights                Deli / Bodega   
19                Cobble Hill                 Cocktail Bar   
20            Carroll Gardens           Italian Restaurant   
21                   Red Hook           Seafood Restaurant   
22                    Gowanus           Italian Restaurant   
23                Fort Greene           Italian Restaurant   
24                 Park Slope                  Coffee Shop   
32               Coney Island             Baseball Stadium   
35              Dyker Heights                  Golf Course   
36            Gerritsen Beach               Ice Cream Shop   
38               Clinton Hill                  Pizza Place   
40                   Downtown                 Burger Joint   
41                Boerum Hill                  Coffee Shop   
42  Prospect Lefferts Gardens                         Café   
43                 Ocean Hill                Deli / Bodega   
44                  City Line                   Donut Shop   
49          East Williamsburg                          Bar   
50                 North Side                  Coffee Shop   
51                 South Side                          Bar   
54                Ditmas Park                 Burger Joint   
55                    Wingate          Fried Chicken Joint   
59            Paerdegat Basin             Business Service   
61               Fulton Ferry                         Park   
62               Vinegar Hill                   Food Truck   
64          Broadway Junction                   Donut Shop   
65                      Dumbo                         Park   
67              Highland Park                Deli / Bodega   

   2nd Most Common Venue            3rd Most Common Venue  \
0                    Spa               Italian Restaurant   
1     Italian Restaurant                       Donut Shop   
3            Pizza Place                      Coffee Shop   
5             Restaurant                Mobile Phone Shop   
6     Turkish Restaurant                   Sandwich Place   
11       Thai Restaurant                      Pizza Place   
12                 Plaza                    Deli / Bodega   
13    Mexican Restaurant                      Coffee Shop   
15            Bagel Shop                      Coffee Shop   
16         Deli / Bodega                      Coffee Shop   
17         Deli / Bodega                             Café   
18    Italian Restaurant                      Yoga Studio   
19           Coffee Shop                       Playground   
20           Coffee Shop                           Bakery   
21           Art Gallery                              Bar   
22                   Bar           Furniture / Home Store   
23           Flower Shop                        Wine Shop   
24          Burger Joint                       Bagel Shop   
32               Brewery                   Cosmetics Shop   
35         Grocery Store                     Burger Joint   
36                   Bar                  Harbor / Marina   
38    Italian Restaurant                  Thai Restaurant   
40           Coffee Shop                      Pizza Place   
41          Dance Studio                              Bar   
42         Deli / Bodega             Caribbean Restaurant   
43          

In [108]:
print("Queens: Cluster 1")
q_merged.loc[q_merged['Cluster Labels'] == 0, q_merged.columns[[1] + list(range(5, q_merged.shape[1]))]]

Queens: Cluster 1


Neighborhood 1st Most Common Venue 2nd Most Common Venue  \
21   Whitestone       Bubble Tea Shop          Dance Studio   
64   Brookville         Deli / Bodega         Women's Store   

   3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
21         Deli / Bodega           Candy Store           Flower Shop   
64  Fast Food Restaurant     Electronics Store   Empanada Restaurant   

   6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
21                  Food           Flea Market           Fish Market   
64           Event Space    Falafel Restaurant                  Farm   

   9th Most Common Venue 10th Most Common Venue  
21     Electronics Store    Filipino Restaurant  
64        Farmers Market    Filipino Restaurant

In [109]:
print("Queens: Cluster 2")
q_merged.loc[q_merged['Cluster Labels'] == 1, q_merged.columns[[1] + list(range(5, q_merged.shape[1]))]]

Queens: Cluster 2


Neighborhood 1st Most Common Venue 2nd Most Common Venue  \
43  Breezy Point                 Beach   Monument / Landmark   
50      Neponsit                 Beach         Women's Store   

          3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
43                        Trail              Bus Stop         Women's Store   
50  Eastern European Restaurant                  Food           Flower Shop   

   6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
43        Farmers Market   Empanada Restaurant           Event Space   
50           Flea Market           Fish Market     Fish & Chips Shop   

   9th Most Common Venue 10th Most Common Venue  
43    Falafel Restaurant                   Farm  
50   Filipino Restaurant   Fast Food Restaurant

In [110]:
print("Queens: Cluster 3")
q_merged.loc[q_merged['Cluster Labels'] == 2, q_merged.columns[[1] + list(range(5, q_merged.shape[1]))]]

Queens: Cluster 3


Neighborhood            1st Most Common Venue  \
0                Astoria                              Bar   
1               Woodside                    Grocery Store   
2        Jackson Heights        Latin American Restaurant   
3               Elmhurst                  Thai Restaurant   
4           Howard Beach               Italian Restaurant   
5                 Corona               Mexican Restaurant   
6           Forest Hills                              Gym   
7            Kew Gardens               Chinese Restaurant   
8          Richmond Hill                      Pizza Place   
9               Flushing                  Bubble Tea Shop   
10      Long Island City                            Hotel   
11             Sunnyside                      Pizza Place   
12         East Elmhurst                       Donut Shop   
13               Maspeth                            Diner   
14             Ridgewood                         Pharmacy   
15              Glendale                      Pizza Place   
16             Rego Park                           Bakery   
17             Woodhaven                    Deli / Bodega   
18            Ozone Park                         Pharmacy   
19      South Ozone Park                             Park   
20         College Point                    Deli / Bodega   
22               Bayside                              Bar   
23            Auburndale               Italian Restaurant   
24           Little Neck               Chinese Restaurant   
25            Douglaston                      Pizza Place   
26             Glen Oaks                         Pharmacy   
27             Bellerose                    Deli / Bodega   
28     Kew Gardens Hills                             Bank   
29         Fresh Meadows                      Bus Station   
30             Briarwood                    Deli / Bodega   
31        Jamaica Center                   Clothing Store   
32       Oakland Gardens                Korean Restaurant   
33        Queens Village                         Bus Stop   
34                Hollis                             Park   
35         South Jamaica                      Bus Station   
36            St. Albans             Caribbean Restaurant   
37              Rochdale  Southern / Soul Food Restaurant   
38   Springfield Gardens                      Bus Station   
39       Cambria Heights             Caribbean Restaurant   
40              Rosedale                      Bus Station   
41          Far Rockaway                    Deli / Bodega   
42         Broad Channel              Sporting Goods Shop   
44              Steinway              Rental Car Location   
45            Beechhurst                      Yoga Studio   
46           Bay Terrace                   Clothing Store   
47              Edgemere                    Metro Station   
48               Arverne                        Surf Spot   
49        Rockaway Beach                            Beach   
51           Murray Hill                Korean Restaurant   
52           Floral Park                Indian Restaurant   
53            Holliswood                       Playground   
54       Jamaica Estates                          Dog Run   
55       Queensboro Hill               Chinese Restaurant   
56             Hillcrest        College Academic Building   
57            Ravenswood               Chinese Restaurant   
58            Lindenwood              Japanese Restaurant   
59             Laurelton             Caribbean Restaurant   
60           Lefrak City                   Cosmetics Shop   
61          Belle Harbor                            Beach   
62         Rockaway Park                            Beach   
65              Bellaire               Chinese Restaurant   
66          North Corona                    Deli / Bodega   
67  Forest Hills Gardens                         Pharmacy   
68         Jamaica Hills                         Pharmacy   
69                Utopia                    Del

In [111]:
print("Queens: Cluster 4")
q_merged.loc[q_merged['Cluster Labels'] == 3, q_merged.columns[[1] + list(range(5, q_merged.shape[1]))]]

Queens: Cluster 4


Neighborhood 1st Most Common Venue 2nd Most Common Venue  \
63   Somerville                  Park         Women's Store   

   3rd Most Common Venue        4th Most Common Venue 5th Most Common Venue  \
63                  Farm  Eastern European Restaurant     Electronics Store   

   6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
63   Empanada Restaurant           Event Space    Falafel Restaurant   

   9th Most Common Venue 10th Most Common Venue  
63        Farmers Market            Dry Cleaner

In [112]:
print("Queens: Cluster 5")
q_merged.loc[q_merged['Cluster Labels'] == 4, q_merged.columns[[1] + list(range(5, q_merged.shape[1]))]]

Queens: Cluster 5


Neighborhood 1st Most Common Venue 2nd Most Common Venue  \
77        Malba          Tennis Court              Bus Line   
79    Bayswater          Tennis Court            Playground   

   3rd Most Common Venue        4th Most Common Venue  \
77             Rest Area                         Farm   
79        Farmers Market  Eastern European Restaurant   

          5th Most Common Venue 6th Most Common Venue 7th Most Common Venue  \
77  Eastern European Restaurant     Electronics Store   Empanada Restaurant   
79            Electronics Store   Empanada Restaurant           Event Space   

   8th Most Common Venue 9th Most Common Venue 10th Most Common Venue  
77           Event Space    Falafel Restaurant          Women's Store  
79    Falafel Restaurant                  Farm          Women's Store

In [113]:
print("Bronx: Cluster 1")
bx_merged.loc[bx_merged['Cluster Labels'] == 0, bx_merged.columns[[1] + list(range(5, bx_merged.shape[1]))]]

Bronx: Cluster 1


Neighborhood 1st Most Common Venue   2nd Most Common Venue  \
0            Wakefield              Pharmacy          Ice Cream Shop   
6             Woodlawn         Deli / Bodega       Food & Drink Shop   
7              Norwood           Pizza Place                    Park   
10      Pelham Parkway           Pizza Place      Italian Restaurant   
11         City Island    Seafood Restaurant  Thrift / Vintage Store   
14      Morris Heights    Spanish Restaurant             Pizza Place   
16        East Tremont           Pizza Place          Cosmetics Shop   
19             Melrose           Pizza Place          Sandwich Place   
20          Mott Haven           Pizza Place                     Gym   
23         Hunts Point           Pizza Place           Grocery Store   
27         Throgs Neck           Pizza Place                     Bar   
29         Parkchester           Supermarket             Pizza Place   
30  Westchester Square  Fast Food Restaurant                Pharmacy   
31            Van Nest         Deli / Bodega             Pizza Place   
32         Morris Park           Pizza Place                  Bakery   
33             Belmont    Italian Restaurant             Pizza Place   
34      Spuyten Duyvil         Deli / Bodega        Asian Restaurant   
35     North Riverdale           Pizza Place      Italian Restaurant   
36          Pelham Bay                  Bank      Italian Restaurant   
37       Schuylerville           Pizza Place      Mexican Restaurant   
38      Edgewater Park    Italian Restaurant             Pizza Place   
39         Castle Hill                 Diner             Pizza Place   
41      Pelham Gardens              Pharmacy             Pizza Place   
47          Mount Eden              Pharmacy             Pizza Place   
49           Bronxdale        Breakfast Spot                    Bank   

        3rd Most Common Venue          4th Most Common Venue  \
0                  Laundromat                   Dessert Shop   
6                         Bar                     Playground   
7                        Bank                       Pharmacy   
10         Chinese Restaurant                   Home Service   
11             History Museum               Tapas Restaurant   
14                   Pharmacy                  Grocery Store   
16               Intersection                           Café   
19                   Pharmacy                  Grocery Store   
20                 Donut Shop             Spanish Restaurant   
23         Spanish Restaurant                           Food   
27              Deli / Bodega            American Restaurant   
29                 Kids Store                           Bank   
30         Mexican Restaurant                 Sandwich Place   
31  Middle Eastern Restaurant                      BBQ Joint   
32              Deli / Bodega                   Burger Joint   
33              Deli / Bodega                         Bakery   
34                   Bus Line                    Pizza Place   
35         Chinese Restaurant                           Bank   
36          Convenience Store                 Sandwich Place   
37                      Diner                       Pharmacy   
38              Deli / Bodega                            Bar   
39                   Pharmacy                         Market   
41                Bus Station            American Restaurant   
47              Deli / Bodega                            Bar   
49      Performing Arts Venue  Paper / Office Supplies Store   

   5th Most Common Venue        6th Most Common Venue  7th Most Common Venue  \
0         Sandwich Place                   Donut Shop            Gas Station   
6                    Pub                  Pizza Place     Italian Restaurant   
7             Restaurant                      Library     Mexican Restaurant   
10           Gas Station                Deli / Bodega  Performing Arts Venue   
11         Deli / Bodega                     Pharmacy            Pizza P

In [114]:
print("Bronx: Cluster 2")
bx_merged.loc[bx_merged['Cluster Labels'] == 1, bx_merged.columns[[1] + list(range(5, bx_merged.shape[1]))]]

Bronx: Cluster 2


Neighborhood 1st Most Common Venue 2nd Most Common Venue  \
3    Fieldston                 Plaza  Medical Supply Store   
4    Riverdale           Bus Station                  Park   

  3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
3                 River           Bus Station     Electronics Store   
4                 Plaza  Medical Supply Store        Baseball Field   

  6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
3                  Food           Fish Market     Fish & Chips Shop   
4                   Gym                  Bank        Farmers Market   

  9th Most Common Venue 10th Most Common Venue  
3           Film Studio   Fast Food Restaurant  
4                  Food            Fish Market

In [115]:
print("Bronx: Cluster 3")
bx_merged.loc[bx_merged['Cluster Labels'] == 2, bx_merged.columns[[1] + list(range(5, bx_merged.shape[1]))]]

Bronx: Cluster 3


Neighborhood   1st Most Common Venue      2nd Most Common Venue  \
1            Co-op City    Fast Food Restaurant          Accessories Store   
2           Eastchester    Caribbean Restaurant                Bus Station   
5           Kingsbridge             Pizza Place                     Bakery   
8        Williamsbridge           Metro Station                        Bar   
9            Baychester              Donut Shop         Spanish Restaurant   
12         Bedford Park           Deli / Bodega                      Diner   
13   University Heights             Pizza Place  Latin American Restaurant   
15              Fordham      Spanish Restaurant          Mobile Phone Shop   
17           West Farms             Bus Station                 Donut Shop   
18         High  Bridge      Chinese Restaurant                   Pharmacy   
21          Port Morris  Furniture / Home Store                 Donut Shop   
22             Longwood    Fast Food Restaurant              Deli / Bodega   
24           Morrisania          Discount Store                Bus Station   
25            Soundview      Chinese Restaurant              Grocery Store   
40            Olinville    Caribbean Restaurant        Fried Chicken Joint   
42            Concourse           Grocery Store         Spanish Restaurant   
43            Unionport          Ice Cream Shop  Latin American Restaurant   
44             Edenwald           Grocery Store                Supermarket   
45    Claremont Village             Bus Station              Grocery Store   
46    Concourse Village          Sandwich Place       Fast Food Restaurant   
48           Mount Hope           Grocery Store             Ice Cream Shop   
50             Allerton             Pizza Place              Deli / Bodega   
51  Kingsbridge Heights      Mexican Restaurant                Pizza Place   

        3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
1              Baseball Field         Grocery Store   Fried Chicken Joint   
2                       Diner         Deli / Bodega         Bowling Alley   
5              Sandwich Place                   Bar    Mexican Restaurant   
8                  Soup Place             Nightclub  Caribbean Restaurant   
9        Fast Food Restaurant         Boat or Ferry        Mattress Store   
12         Mexican Restaurant           Bus Station        Sandwich Place   
13                 Donut Shop    Chinese Restaurant        Sandwich Place   
15                 Donut Shop                  Bank            Shoe Store   
17         Chinese Restaurant                  Park          Intersection   
18         Spanish Restaurant           Bus Station           Pizza Place   
21              Grocery Store         Metro Station      Storage Facility   
22         Chinese Restaurant         Tattoo Parlor            Donut Shop   
24       Fast Food Restaurant            Donut Shop          Intersection   
25  Latin American Restaurant            Playground           Bus Station   
40               Liquor Store         Deli / Bodega                  Food   
42                Pizza Place   Fried Chicken Joint                Bakery   
43                 Donut Shop  Caribbean Restaurant     Indian Restaurant   
44                Fish Market           Bus Station    Athletics & Sports   
45              Deli / Bodega                Bakery                  Park   
46         Mexican Restaurant           Pizza Place   Sporting Goods Shop   
48         Chinese Restaurant        Sandwich Place            Donut Shop   
50                Supermarket    Chinese Restaurant                   Spa   
51         Chinese Restaurant         Grocery Store   Fried Chicken Joint   

        6th Most Common Venue      7th Most Common Venue  \
1                        Park             Discount Store   
2           Convenience Store                 Donut Shop   
5   Latin American Restaurant                 Donut Shop   
8                  Distillery                Film

In [116]:
print("Bronx: Cluster 4")
bx_merged.loc[bx_merged['Cluster Labels'] == 3, bx_merged.columns[[1] + list(range(5, bx_merged.shape[1]))]]

Bronx: Cluster 4


Neighborhood 1st Most Common Venue 2nd Most Common Venue  \
28  Country Club        Sandwich Place    Athletics & Sports   

   3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
28            Playground                 Trail            Donut Shop   

   6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
28                  Food           Fish Market     Fish & Chips Shop   

   9th Most Common Venue 10th Most Common Venue  
28           Film Studio   Fast Food Restaurant

In [117]:
print("Bronx: Cluster 5")
bx_merged.loc[bx_merged['Cluster Labels'] == 4, bx_merged.columns[[1] + list(range(5, bx_merged.shape[1]))]]

Bronx: Cluster 5


Neighborhood 1st Most Common Venue 2nd Most Common Venue  \
26  Clason Point                  Park         Grocery Store   

        3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
26  South American Restaurant         Boat or Ferry              Bus Stop   

   6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
26                  Pool     Convenience Store        Discount Store   

   9th Most Common Venue 10th Most Common Venue  
26        Farmers Market       Department Store